In [1]:
import pandas as pd
import numpy as np
import ast
import statsmodels.api as sm
pd.set_option('display.max_columns',None)
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.linear_model import LinearRegression as LRN
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.utils import resample
from sklearn.metrics import confusion_matrix
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import confusion_matrix
from sklearn.decomposition import PCA
import matplotlib.pyplot as plt
from sklearn.tree import DecisionTreeRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import cross_val_score
from sklearn.linear_model import LogisticRegression as LinReg
from sklearn.metrics import mean_absolute_error as mae

### 1. Insert the data 

In [2]:
data = pd.read_csv('dataset.csv', encoding='latin-1')
print(data.shape)
data.head()

(1000, 7)


Unnamed: 0                                 title  \
0        1999                   Swedish Baked Beans   
1        2000                      Carrot Casserole   
2        2001  Melt In Your Mouth Chicken Casserole   
3        2002                    Autumn Apple Salad   
4        2003                   Macaroni And Cheese   

                                         ingredients  \
0  ["2 lb. dry pinto beans", "1/2 c. cooking oil"...   
1  ["2 c. grated raw carrots", "2 eggs, beaten", ...   
2  ["2 1/2 to 3 lb. chicken, cooked and deboned (...   
3  ["1 (20 oz.) can crushed pineapple (undrained)...   
4  ["1 (8 oz.) box elbow macaroni", "3 c. grated ...   

                                          directions  \
0  ["Cook pinto beans for 2 1/2 hours, then drain...   
1  ["Mix together well.", "Bake in buttered casse...   
2  ["Preheat oven to 425\u00b0.", "In oblong baki...   
3  ["In a saucepan, combine pineapple and sugar; ...   
4  ["Cook macaroni until done; drain. Grate chees...   

                                              link    source  \
0  www.cookbooks.com/Recipe-Details.aspx?id=710520  Gathered   
1  www.cookbooks.com/Recipe-Details.aspx?id=982285  Gathered   
2  www.cookbooks.com/Recipe-Details.aspx?id=493659  Gathered   
3  www.cookbooks.com/Recipe-Details.aspx?id=596076  Gathered   
4    www.cookbooks.com/Recipe-Details.aspx?id=9087  Gathered   

                                                 NER  
0  ["pinto beans", "cooking oil", "catsup", "Worc...  
1  ["carrots", "eggs", "grated cheese", "cracker ...  
2  ["chicken", "cream of chicken", "margarine", "...  
3  ["pineapple", "sugar", "lemon flavored gelatin...  
4  ["elbow macaroni", "grated cheese", "eggs", "b...

### 2. Cleaning the column name

In [3]:
data.columns

Index(['Unnamed: 0', 'title', 'ingredients', 'directions', 'link', 'source',
       'NER'],
      dtype='object')

In [4]:
data.rename(columns={data.columns[0]: 'id'}, inplace=True)


In [5]:
data.rename(columns={data.columns[6]: 'item'}, inplace=True)

In [6]:
data.columns

Index(['id', 'title', 'ingredients', 'directions', 'link', 'source', 'item'], dtype='object')

In [7]:
data.head()

id                                 title  \
0  1999                   Swedish Baked Beans   
1  2000                      Carrot Casserole   
2  2001  Melt In Your Mouth Chicken Casserole   
3  2002                    Autumn Apple Salad   
4  2003                   Macaroni And Cheese   

                                         ingredients  \
0  ["2 lb. dry pinto beans", "1/2 c. cooking oil"...   
1  ["2 c. grated raw carrots", "2 eggs, beaten", ...   
2  ["2 1/2 to 3 lb. chicken, cooked and deboned (...   
3  ["1 (20 oz.) can crushed pineapple (undrained)...   
4  ["1 (8 oz.) box elbow macaroni", "3 c. grated ...   

                                          directions  \
0  ["Cook pinto beans for 2 1/2 hours, then drain...   
1  ["Mix together well.", "Bake in buttered casse...   
2  ["Preheat oven to 425\u00b0.", "In oblong baki...   
3  ["In a saucepan, combine pineapple and sugar; ...   
4  ["Cook macaroni until done; drain. Grate chees...   

                                              link    source  \
0  www.cookbooks.com/Recipe-Details.aspx?id=710520  Gathered   
1  www.cookbooks.com/Recipe-Details.aspx?id=982285  Gathered   
2  www.cookbooks.com/Recipe-Details.aspx?id=493659  Gathered   
3  www.cookbooks.com/Recipe-Details.aspx?id=596076  Gathered   
4    www.cookbooks.com/Recipe-Details.aspx?id=9087  Gathered   

                                                item  
0  ["pinto beans", "cooking oil", "catsup", "Worc...  
1  ["carrots", "eggs", "grated cheese", "cracker ...  
2  ["chicken", "cream of chicken", "margarine", "...  
3  ["pineapple", "sugar", "lemon flavored gelatin...  
4  ["elbow macaroni", "grated cheese", "eggs", "b...

### 3. Checking the data (Nan, Object, unique)

In [8]:
data.isna().sum()

id             0
title          0
ingredients    0
directions     0
link           0
source         0
item           0
dtype: int64

In [9]:
data.dtypes

id              int64
title          object
ingredients    object
directions     object
link           object
source         object
item           object
dtype: object

In [10]:
data['id'].value_counts(dropna=False)

1999    1
2670    1
2657    1
2658    1
2659    1
       ..
2337    1
2338    1
2339    1
2340    1
2998    1
Name: id, Length: 1000, dtype: int64

In [11]:
# Check if there are any duplicated values in the 'ID' column
are_ids_unique = not data['id'].duplicated().any()

if are_ids_unique:
    print("All values in the 'id' column are unique.")
else:
    print("There are duplicated values in the 'id' column.")


All values in the 'id' column are unique.


In [12]:
data1 = pd.DataFrame(data)
data1.head()

id                                 title  \
0  1999                   Swedish Baked Beans   
1  2000                      Carrot Casserole   
2  2001  Melt In Your Mouth Chicken Casserole   
3  2002                    Autumn Apple Salad   
4  2003                   Macaroni And Cheese   

                                         ingredients  \
0  ["2 lb. dry pinto beans", "1/2 c. cooking oil"...   
1  ["2 c. grated raw carrots", "2 eggs, beaten", ...   
2  ["2 1/2 to 3 lb. chicken, cooked and deboned (...   
3  ["1 (20 oz.) can crushed pineapple (undrained)...   
4  ["1 (8 oz.) box elbow macaroni", "3 c. grated ...   

                                          directions  \
0  ["Cook pinto beans for 2 1/2 hours, then drain...   
1  ["Mix together well.", "Bake in buttered casse...   
2  ["Preheat oven to 425\u00b0.", "In oblong baki...   
3  ["In a saucepan, combine pineapple and sugar; ...   
4  ["Cook macaroni until done; drain. Grate chees...   

                                              link    source  \
0  www.cookbooks.com/Recipe-Details.aspx?id=710520  Gathered   
1  www.cookbooks.com/Recipe-Details.aspx?id=982285  Gathered   
2  www.cookbooks.com/Recipe-Details.aspx?id=493659  Gathered   
3  www.cookbooks.com/Recipe-Details.aspx?id=596076  Gathered   
4    www.cookbooks.com/Recipe-Details.aspx?id=9087  Gathered   

                                                item  
0  ["pinto beans", "cooking oil", "catsup", "Worc...  
1  ["carrots", "eggs", "grated cheese", "cracker ...  
2  ["chicken", "cream of chicken", "margarine", "...  
3  ["pineapple", "sugar", "lemon flavored gelatin...  
4  ["elbow macaroni", "grated cheese", "eggs", "b...

In [14]:
data1.to_csv('data1.csv')

### 4. Make a new DF for item for scalling

In [35]:
factor = pd.DataFrame(data['item'])
print(factor.shape)
factor.head(10)

(1000, 1)


item
0  ["pinto beans", "cooking oil", "catsup", "Worc...
1  ["carrots", "eggs", "grated cheese", "cracker ...
2  ["chicken", "cream of chicken", "margarine", "...
3  ["pineapple", "sugar", "lemon flavored gelatin...
4  ["elbow macaroni", "grated cheese", "eggs", "b...
5  ["shortening", "peanut butter", "sugar", "brow...
6  ["butter", "chocolate chips", "egg", "confecti...
7  ["tomatoes", "bacon", "mayonnaise", "green oni...
8  ["ground beef", "tomato sauce", "taco", "corn ...
9  ["green chili peppers", "eggs", "Cheddar chees...

In [36]:
# Apply lower() function to each item in the 'item' column
factor['item'] = factor['item'].apply(lambda x: [ingredient.lower() for ingredient in eval(x)])

factor.head()


item
0  [pinto beans, cooking oil, catsup, worcestersh...
1  [carrots, eggs, grated cheese, cracker crumbs,...
2  [chicken, cream of chicken, margarine, flour, ...
3  [pineapple, sugar, lemon flavored gelatin, cre...
4  [elbow macaroni, grated cheese, eggs, butter, ...

In [37]:
factor.to_csv('item.csv')

In [38]:
s = factor['item'].explode()
s

0               pinto beans
0               cooking oil
0                    catsup
0      worcestershire sauce
0                  molasses
               ...         
999                 vanilla
999                   flour
999                    salt
999                    soda
999                 peanuts
Name: item, Length: 7349, dtype: object

In [39]:
pd.set_option('display.max_columns', None)
factor1 = factor[['item']].join(pd.crosstab(s.index, s))
print(factor1.shape)
factor1.head()

(1000, 1122)


item  's secret ingredients  \
0  [pinto beans, cooking oil, catsup, worcestersh...                    0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...                    0.0   
2  [chicken, cream of chicken, margarine, flour, ...                    0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...                    0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...                    0.0   

     +  accent  accent seasonings  active dry yeast  all-purpose  \
0  0.0     0.0                0.0               0.0          0.0   
1  0.0     0.0                0.0               0.0          0.0   
2  0.0     0.0                0.0               0.0          0.0   
3  0.0     0.0                0.0               0.0          0.0   
4  0.0     0.0                0.0               0.0          0.0   

   all-purpose flour  allspice  almond  almond extract  almond flavoring  \
0                0.0       0.0     0.0             0.0               0.0   
1                0.0       0.0     0.0             0.0               0.0   
2                0.0       0.0     0.0             0.0               0.0   
3                0.0       0.0     0.0             0.0               0.0   
4                0.0       0.0     0.0             0.0               0.0   

   almonds  american cheese  angel  angel food cake  anise seed  apple  \
0      0.0              0.0    0.0              0.0         0.0    0.0   
1      0.0              0.0    0.0              0.0         0.0    0.0   
2      0.0              0.0    0.0              0.0         0.0    0.0   
3      0.0              0.0    0.0              0.0         0.0    0.0   
4      0.0              0.0    0.0              0.0         0.0    0.0   

   apple cider  apple juice  apple pie filling  apple wedges  apples  \
0          0.0          0.0                0.0           0.0     0.0   
1          0.0          0.0                0.0           0.0     0.0   
2          0.0          0.0                0.0           0.0     0.0   
3          0.0          0.0                0.0           0.0     0.0   
4          0.0          0.0                0.0           0.0     0.0   

   applesauce  apricot preserves  artichokes  au jus  avocado  avocados  \
0         0.0                0.0         0.0     0.0      0.0       0.0   
1         0.0                0.0         0.0     0.0      0.0       0.0   
2         0.0                0.0         0.0     0.0      0.0       0.0   
3         0.0                0.0         0.0     0.0      0.0       0.0   
4         0.0                0.0         0.0     0.0      0.0       0.0   

   baby shrimp  bacon  bacon bits  bacon drippings  bacon grease  \
0          0.0    0.0         0.0              0.0           0.0   
1          0.0    0.0         0.0              0.0           0.0   
2          0.0    0.0         0.0              0.0           0.0   
3          0.0    0.0         0.0              0.0           0.0   
4          0.0    0.0         0.0              0.0           0.0   

   bacon strips  baking apples  baking chocolate  baking mix  baking potatoes  \
0           0.0            0.0               0.0         0.0              0.0   
1           0.0            0.0               0.0         0.0              0.0   
2           0.0            0.0               0.0         0.0              0.0   
3           0.0            0.0               0.0         0.0              0.0   
4           0.0            0.0               0.0         0.0              0.0   

   baking powder  baking soda  bakon slices  balsamic vinegar  banana  \
0            0.0          0.0           0.0               0.0     0.0   
1            0.0          0.0           0.0               0.0     0.0   
2            0.0          0.0           0.0               0.0     0.0   
3            0.0          0.0           0.0               0.0     0.0   
4            0.0          0.0           0.0               0.0     0.0   

   bananas  barbecue  barbecue sauce  basil

In [40]:
# Assuming df is your DataFrame
column_names_list = factor1.columns.tolist()
print('Total item = ', len(column_names_list))
# print(column_names_list)

Total item =  1122


### Drop Unneccesary Columns

In [41]:
drop_columns_list = ["'s secret ingredients",'+','au jus','benne','broth from','broth from ham','buns','caraway seed','chitterlings','cold cola','colored miniature','column','concentrate','containers','cooking oats','crust','crystals','cut rhubarb','deli','dew','dinner rolls','equal amount','fat','feet','fifth','figard liquid smoke','fine cracker crumbs','fixins','flavored jello','fluid','frozen','frozen pie pastry','frozen pound cake','fluid','fryer','grated sharp','green','griffin','grits','ground sage','gummy worms','hamburger','hard rolls','hearts','hi-c','hot fat','i','irish','jicama','jigger','joe','just','kisses','kitchen','krispies','ladyfingers','langostinos','lard','lavender','layer','lean hamburger','leeks','liquid','liquid fruit pectin','liquid shortening','liquid smoke','liquid sweetener','marjoram','marsala','marshmallow cream','marshmallows','meal','meringue',"mini reese's",'miracle','mix','mixed herbs','mixed nuts','mixture','molasses','monde','n', 'nestles','non-caloric', 'nonstick cooking spray','o','oatmeal','oats','okra','oleo','orzo','other shortening','packets equal','packets splenda','paraffin','paraffin wax','pastry','pastry shell','poppy seed','preserves','q','quick grits','red','regular','ro-tel','roll','rolled oats','rye meal','sage','sandies','schilling mexican','shank portion','shells','sherry','shortening','shoyu','soda','sorghum molasses','spice','sprinkles','squirrels','squish','stack','stock','stove top stuffing','stuffing mix','summer squash','sunflower seeds','sweet','tablets','tarragon leaves','tater','thin','thin slices','tightly packed dandelion blossoms','topping','tops','tubs','unflavored gelatin','varieties','velveeta','water chestnuts','watercress','well','white','white karo','wieners','will also','wrappers','young groundhog','your favorite','zinfandel','zita']

In [42]:
len(drop_columns_list)

153

In [43]:
factor2 = factor1.drop(drop_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 970)


item  accent  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0   

   accent seasonings  active dry yeast  all-purpose  all-purpose flour  \
0                0.0               0.0          0.0                0.0   
1                0.0               0.0          0.0                0.0   
2                0.0               0.0          0.0                0.0   
3                0.0               0.0          0.0                0.0   
4                0.0               0.0          0.0                0.0   

   allspice  almond  almond extract  almond flavoring  almonds  \
0       0.0     0.0             0.0               0.0      0.0   
1       0.0     0.0             0.0               0.0      0.0   
2       0.0     0.0             0.0               0.0      0.0   
3       0.0     0.0             0.0               0.0      0.0   
4       0.0     0.0             0.0               0.0      0.0   

   american cheese  angel  angel food cake  anise seed  apple  apple cider  \
0              0.0    0.0              0.0         0.0    0.0          0.0   
1              0.0    0.0              0.0         0.0    0.0          0.0   
2              0.0    0.0              0.0         0.0    0.0          0.0   
3              0.0    0.0              0.0         0.0    0.0          0.0   
4              0.0    0.0              0.0         0.0    0.0          0.0   

   apple juice  apple pie filling  apple wedges  apples  applesauce  \
0          0.0                0.0           0.0     0.0         0.0   
1          0.0                0.0           0.0     0.0         0.0   
2          0.0                0.0           0.0     0.0         0.0   
3          0.0                0.0           0.0     0.0         0.0   
4          0.0                0.0           0.0     0.0         0.0   

   apricot preserves  artichokes  avocado  avocados  baby shrimp  bacon  \
0                0.0         0.0      0.0       0.0          0.0    0.0   
1                0.0         0.0      0.0       0.0          0.0    0.0   
2                0.0         0.0      0.0       0.0          0.0    0.0   
3                0.0         0.0      0.0       0.0          0.0    0.0   
4                0.0         0.0      0.0       0.0          0.0    0.0   

   bacon bits  bacon drippings  bacon grease  bacon strips  baking apples  \
0         0.0              0.0           0.0           0.0            0.0   
1         0.0              0.0           0.0           0.0            0.0   
2         0.0              0.0           0.0           0.0            0.0   
3         0.0              0.0           0.0           0.0            0.0   
4         0.0              0.0           0.0           0.0            0.0   

   baking chocolate  baking mix  baking potatoes  baking powder  baking soda  \
0               0.0         0.0              0.0            0.0          0.0   
1               0.0         0.0              0.0            0.0          0.0   
2               0.0         0.0              0.0            0.0          0.0   
3               0.0         0.0              0.0            0.0          0.0   
4               0.0         0.0              0.0            0.0          0.0   

   bakon slices  balsamic vinegar  banana  bananas  barbecue  barbecue sauce  \
0           0.0               0.0     0.0      0.0       0.0             0.0   
1           0.0               0.0     0.0      0.0       0.0             0.0   
2           0.0               0.0     0.0      0.0       0.0             0.0   
3           0.0               0.0     0.0      0.0       0.0             0.0   
4           0.0               0.0     0.0      0.0       0.0             0.0   

   basil  bay leaf  bay leaves  bay seasoning  ba

### Vegetables group

In [46]:
factor2['vegetables'] = factor2['artichokes']+factor2['basil']+factor2['bay leaf']+factor2['bayleaf']+factor2['bay leaves']+factor2['beets']+ factor2['broccoli']+ factor2['broccoli stems']+factor2['brussels']+factor2['cabbage']+factor2['california']+factor2['carrot']+ factor2['carrot strips']+ factor2['carrots']+factor2['basil']+factor2['cauliflower']+factor2['celery']+factor2['celery salt']+ factor2['chopped lettuce']+ factor2['chopped spinach']+factor2['cole slaw']+factor2['bay leaf']+factor2['cole slaw blend']+factor2['condensed broccoli soup']+ factor2['cucumber']+ factor2['cucumbers']+factor2['eggplant']+factor2['fresh basil']+factor2['fresh parsley']+factor2['fresh spinach']+ factor2['frozen broccoli']+ factor2['frozen spinach']+factor2['head lettuce']+factor2['horseradish']+factor2['lentils']+factor2['lettuce leaves']+ factor2['mixed salad greens']+ factor2['mixed vegetables']+factor2['parsley']+factor2['parsley flakes']+factor2['prunes']+factor2['pumpkin']+ factor2['pumpkin seeds']+ factor2['radishes']+factor2['red cabbage']+factor2['red lentils']+factor2['rhubarb']+factor2['rinsed lentils']+ factor2['romaine lettuce']+factor2['sauerkraut']+factor2['shredded lettuce']+factor2['solid pumpkin']+factor2['spinach']+factor2['sprouts']+factor2['stalks celery']+factor2['torn spinach greens']+factor2['vegetable bouillon']+factor2['vegetable cooking spray']+factor2['vegetable shortening']+factor2['zucchini']+factor2['fresh tomatoes']+factor2['italian tomatoes']+factor2['regular tomato catsup']+factor2['ro-tel tomatoes']+factor2['tomato']+factor2['tomato juice']+factor2['tomato paste']+factor2['tomato salsa']+factor2['tomatoes']+factor2['fresh mushrooms']+factor2['mushroom']+factor2['mushrooms']+factor2['white mushrooms']+factor2['fresh broccoli']+factor2['frozen carrots']

In [47]:
vege_columns_list = ['artichokes','basil','bay leaf','bayleaf','bay leaves','beets','broccoli','broccoli stems','brussels','cabbage','california','carrot','carrot strips','carrots','basil','cauliflower','celery','celery salt','chopped lettuce','chopped spinach','cole slaw','bay leaf','cole slaw blend','condensed broccoli soup','cucumber','cucumbers','eggplant','fresh basil','fresh parsley','fresh spinach','frozen broccoli','frozen spinach','head lettuce','horseradish','lentils','lettuce leaves','mixed salad greens','mixed vegetables','parsley','parsley flakes','prunes','pumpkin','pumpkin seeds','radishes','red cabbage','red lentils','rhubarb','rinsed lentils','romaine lettuce','sauerkraut','shredded lettuce','solid pumpkin','spinach','sprouts','stalks celery','torn spinach greens','vegetable bouillon','vegetable cooking spray','vegetable shortening','zucchini','fresh tomatoes','italian tomatoes','regular tomato catsup','ro-tel tomatoes','tomato','tomato juice','tomato paste','tomato salsa','tomatoes','fresh mushrooms','mushroom','mushrooms','white mushrooms','fresh broccoli','frozen carrots']
len(vege_columns_list)

75

In [48]:
factor2 = factor2.drop(vege_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 898)


item  accent  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0   

   accent seasonings  active dry yeast  all-purpose  all-purpose flour  \
0                0.0               0.0          0.0                0.0   
1                0.0               0.0          0.0                0.0   
2                0.0               0.0          0.0                0.0   
3                0.0               0.0          0.0                0.0   
4                0.0               0.0          0.0                0.0   

   allspice  almond  almond extract  almond flavoring  almonds  \
0       0.0     0.0             0.0               0.0      0.0   
1       0.0     0.0             0.0               0.0      0.0   
2       0.0     0.0             0.0               0.0      0.0   
3       0.0     0.0             0.0               0.0      0.0   
4       0.0     0.0             0.0               0.0      0.0   

   american cheese  angel  angel food cake  anise seed  apple  apple cider  \
0              0.0    0.0              0.0         0.0    0.0          0.0   
1              0.0    0.0              0.0         0.0    0.0          0.0   
2              0.0    0.0              0.0         0.0    0.0          0.0   
3              0.0    0.0              0.0         0.0    0.0          0.0   
4              0.0    0.0              0.0         0.0    0.0          0.0   

   apple juice  apple pie filling  apple wedges  apples  applesauce  \
0          0.0                0.0           0.0     0.0         0.0   
1          0.0                0.0           0.0     0.0         0.0   
2          0.0                0.0           0.0     0.0         0.0   
3          0.0                0.0           0.0     0.0         0.0   
4          0.0                0.0           0.0     0.0         0.0   

   apricot preserves  avocado  avocados  baby shrimp  bacon  bacon bits  \
0                0.0      0.0       0.0          0.0    0.0         0.0   
1                0.0      0.0       0.0          0.0    0.0         0.0   
2                0.0      0.0       0.0          0.0    0.0         0.0   
3                0.0      0.0       0.0          0.0    0.0         0.0   
4                0.0      0.0       0.0          0.0    0.0         0.0   

   bacon drippings  bacon grease  bacon strips  baking apples  \
0              0.0           0.0           0.0            0.0   
1              0.0           0.0           0.0            0.0   
2              0.0           0.0           0.0            0.0   
3              0.0           0.0           0.0            0.0   
4              0.0           0.0           0.0            0.0   

   baking chocolate  baking mix  baking potatoes  baking powder  baking soda  \
0               0.0         0.0              0.0            0.0          0.0   
1               0.0         0.0              0.0            0.0          0.0   
2               0.0         0.0              0.0            0.0          0.0   
3               0.0         0.0              0.0            0.0          0.0   
4               0.0         0.0              0.0            0.0          0.0   

   bakon slices  balsamic vinegar  banana  bananas  barbecue  barbecue sauce  \
0           0.0               0.0     0.0      0.0       0.0             0.0   
1           0.0               0.0     0.0      0.0       0.0             0.0   
2           0.0               0.0     0.0      0.0       0.0             0.0   
3           0.0               0.0     0.0      0.0       0.0             0.0   
4           0.0               0.0     0.0      0.0       0.0             0.0   

   bay seasoning  bean dip  bean sprouts  beans  beef  beef bouillon  \
0            0.0       0.0           0.0    0.0  

### Seasonings Group

In [49]:
factor2['seasonings'] = factor2['accent']+factor2['accent seasonings']+factor2['allspice']+factor2['anise seed']+factor2['bay seasoning']+ factor2['bon']+ factor2['bouillon']+factor2['bouillon cube']+factor2['capers']+factor2['chives']+factor2['chutney']+ factor2['cilantro']+ factor2['cinnamon']+factor2['cloves']+factor2['coloring']+factor2['coriander']+ factor2['cubes']+ factor2['cumin']+factor2['dill']+factor2['dill weed']+factor2['fennel']+factor2['freeze dried chives']+ factor2['fresh chives']+ factor2['fresh cilantro']+factor2['freshly grated nutmeg']+factor2['green food coloring']+factor2["griffin's honey"]+factor2['ground cinnamon']+ factor2['ground cloves']+ factor2['ground cumin']+factor2['ground nutmeg']+factor2['ground oregano']+factor2['honey']+factor2['italian seasoning']+ factor2['kosher salt']+ factor2['mixed spices']+factor2['morton tender quick salt']+factor2['natural honey']+factor2['nutmeats']+factor2['nutmeg']+ factor2['oregano']+ factor2['poultry seasoning']+factor2['red food coloring']+factor2['regular salt']+factor2['rosemary']+factor2['salt']+ factor2['season-all']+factor2['sesame seed']+factor2['sesame seeds']+factor2['thyme']+factor2['turmeric']+factor2['whole allspice']+factor2['whole cloves']+factor2['yellow food coloring']

In [50]:
sea_columns_list = ['accent','accent seasonings','allspice','anise seed','bay seasoning','bon','bouillon','bouillon cube','capers','chives','chutney','cilantro','cinnamon','cloves','coloring','coriander','cubes','cumin','dill','dill weed','fennel','freeze dried chives','fresh chives','fresh cilantro','freshly grated nutmeg','green food coloring',"griffin's honey",'ground cinnamon','ground cloves','ground cumin','ground nutmeg','ground oregano','honey','italian seasoning','kosher salt','mixed spices','morton tender quick salt','natural honey','nutmeats','nutmeg','oregano','poultry seasoning','red food coloring','regular salt','rosemary','salt','season-all','sesame seed','sesame seeds','thyme','turmeric','whole allspice','whole cloves','yellow food coloring']
len(sea_columns_list)

54

In [51]:
factor2 = factor2.drop(sea_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 845)


item  active dry yeast  \
0  [pinto beans, cooking oil, catsup, worcestersh...               0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...               0.0   
2  [chicken, cream of chicken, margarine, flour, ...               0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...               0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...               0.0   

   all-purpose  all-purpose flour  almond  almond extract  almond flavoring  \
0          0.0                0.0     0.0             0.0               0.0   
1          0.0                0.0     0.0             0.0               0.0   
2          0.0                0.0     0.0             0.0               0.0   
3          0.0                0.0     0.0             0.0               0.0   
4          0.0                0.0     0.0             0.0               0.0   

   almonds  american cheese  angel  angel food cake  apple  apple cider  \
0      0.0              0.0    0.0              0.0    0.0          0.0   
1      0.0              0.0    0.0              0.0    0.0          0.0   
2      0.0              0.0    0.0              0.0    0.0          0.0   
3      0.0              0.0    0.0              0.0    0.0          0.0   
4      0.0              0.0    0.0              0.0    0.0          0.0   

   apple juice  apple pie filling  apple wedges  apples  applesauce  \
0          0.0                0.0           0.0     0.0         0.0   
1          0.0                0.0           0.0     0.0         0.0   
2          0.0                0.0           0.0     0.0         0.0   
3          0.0                0.0           0.0     0.0         0.0   
4          0.0                0.0           0.0     0.0         0.0   

   apricot preserves  avocado  avocados  baby shrimp  bacon  bacon bits  \
0                0.0      0.0       0.0          0.0    0.0         0.0   
1                0.0      0.0       0.0          0.0    0.0         0.0   
2                0.0      0.0       0.0          0.0    0.0         0.0   
3                0.0      0.0       0.0          0.0    0.0         0.0   
4                0.0      0.0       0.0          0.0    0.0         0.0   

   bacon drippings  bacon grease  bacon strips  baking apples  \
0              0.0           0.0           0.0            0.0   
1              0.0           0.0           0.0            0.0   
2              0.0           0.0           0.0            0.0   
3              0.0           0.0           0.0            0.0   
4              0.0           0.0           0.0            0.0   

   baking chocolate  baking mix  baking potatoes  baking powder  baking soda  \
0               0.0         0.0              0.0            0.0          0.0   
1               0.0         0.0              0.0            0.0          0.0   
2               0.0         0.0              0.0            0.0          0.0   
3               0.0         0.0              0.0            0.0          0.0   
4               0.0         0.0              0.0            0.0          0.0   

   bakon slices  balsamic vinegar  banana  bananas  barbecue  barbecue sauce  \
0           0.0               0.0     0.0      0.0       0.0             0.0   
1           0.0               0.0     0.0      0.0       0.0             0.0   
2           0.0               0.0     0.0      0.0       0.0             0.0   
3           0.0               0.0     0.0      0.0       0.0             0.0   
4           0.0               0.0     0.0      0.0       0.0             0.0   

   bean dip  bean sprouts  beans  beef  beef bouillon  beef broth  beef chuck  \
0       0.0           0.0    0.0   0.0            0.0         0.0         0.0   
1       0.0           0.0    0.0   0.0            0.0         0.0         0.0   
2       0.0           0.0    0.0   0.0            0.0         0.0         0.0   
3       0.0           0.0    0.0   0.0            0.0         0.0         0.0   
4       0.0           0.0    0.0   0.0   

### Fruit group

In [52]:
factor2['fruits'] = factor2['apricot preserves']+factor2['avocado']+factor2['avocados']+factor2['banana']+factor2['bananas']+ factor2['bing cherries']+ factor2['blackberries']+factor2['blueberries']+factor2['blueberry pie filling']+factor2['candied cherries']+factor2['candied pineapple']+ factor2['cantaloupes']+ factor2['cherries']+factor2['cherry']+factor2['cherry chip cake']+factor2['cherry jello']+ factor2['cherry pie filling']+ factor2['cranberries']+factor2['cranberry juice']+factor2['cranberry salad']+factor2['cranberry sauce']+factor2['dark raisins']+ factor2['dates']+ factor2['fresh cranberries']+factor2['fresh peaches']+factor2['fresh strawberries']+factor2['frozen strawberries']+factor2['fruit cocktail']+ factor2['golden raisins']+ factor2['green grapes']+factor2['ground cranberries']+factor2['maraschino cherries']+factor2['mixed candied fruit']+factor2['overripe bananas']+ factor2['peaches']+ factor2['pears']+factor2['peck pears']+factor2['pineapple']+factor2['pineapple tidbits']+factor2['raisins']+ factor2['raspberry']+ factor2['raspberry jello']+factor2['red grapes']+factor2['seeded raisins']+factor2['strawberries']+factor2['strawberry']+ factor2['strawberry flavored gelatin']+factor2['strawberry jello']+factor2['strawberry preserves']+factor2['strawberry-banana']+factor2['very ripe bananas']+factor2['whole strawberries']+factor2['yellow raisins']+factor2['fruit juice']

In [53]:
fruit_columns_list = ['apricot preserves','avocado','avocados','banana','bananas','bing cherries','blackberries','blueberries','blueberry pie filling','candied cherries','candied pineapple','cantaloupes','cherries','cherry','cherry chip cake','cherry jello','cherry pie filling','cranberries','cranberry juice','cranberry salad','cranberry sauce','dark raisins','dates','fresh cranberries','fresh peaches','fresh strawberries','frozen strawberries','fruit cocktail','golden raisins','green grapes','ground cranberries','maraschino cherries','mixed candied fruit','overripe bananas','peaches','pears','peck pears','pineapple','pineapple tidbits','raisins','raspberry','raspberry jello','red grapes','seeded raisins','strawberries','strawberry','strawberry flavored gelatin','strawberry jello','strawberry preserves','strawberry-banana','very ripe bananas','whole strawberries','yellow raisins','fruit juice']
len(fruit_columns_list)

54

In [54]:
factor2 = factor2.drop(fruit_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 792)


item  active dry yeast  \
0  [pinto beans, cooking oil, catsup, worcestersh...               0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...               0.0   
2  [chicken, cream of chicken, margarine, flour, ...               0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...               0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...               0.0   

   all-purpose  all-purpose flour  almond  almond extract  almond flavoring  \
0          0.0                0.0     0.0             0.0               0.0   
1          0.0                0.0     0.0             0.0               0.0   
2          0.0                0.0     0.0             0.0               0.0   
3          0.0                0.0     0.0             0.0               0.0   
4          0.0                0.0     0.0             0.0               0.0   

   almonds  american cheese  angel  angel food cake  apple  apple cider  \
0      0.0              0.0    0.0              0.0    0.0          0.0   
1      0.0              0.0    0.0              0.0    0.0          0.0   
2      0.0              0.0    0.0              0.0    0.0          0.0   
3      0.0              0.0    0.0              0.0    0.0          0.0   
4      0.0              0.0    0.0              0.0    0.0          0.0   

   apple juice  apple pie filling  apple wedges  apples  applesauce  \
0          0.0                0.0           0.0     0.0         0.0   
1          0.0                0.0           0.0     0.0         0.0   
2          0.0                0.0           0.0     0.0         0.0   
3          0.0                0.0           0.0     0.0         0.0   
4          0.0                0.0           0.0     0.0         0.0   

   baby shrimp  bacon  bacon bits  bacon drippings  bacon grease  \
0          0.0    0.0         0.0              0.0           0.0   
1          0.0    0.0         0.0              0.0           0.0   
2          0.0    0.0         0.0              0.0           0.0   
3          0.0    0.0         0.0              0.0           0.0   
4          0.0    0.0         0.0              0.0           0.0   

   bacon strips  baking apples  baking chocolate  baking mix  baking potatoes  \
0           0.0            0.0               0.0         0.0              0.0   
1           0.0            0.0               0.0         0.0              0.0   
2           0.0            0.0               0.0         0.0              0.0   
3           0.0            0.0               0.0         0.0              0.0   
4           0.0            0.0               0.0         0.0              0.0   

   baking powder  baking soda  bakon slices  balsamic vinegar  barbecue  \
0            0.0          0.0           0.0               0.0       0.0   
1            0.0          0.0           0.0               0.0       0.0   
2            0.0          0.0           0.0               0.0       0.0   
3            0.0          0.0           0.0               0.0       0.0   
4            0.0          0.0           0.0               0.0       0.0   

   barbecue sauce  bean dip  bean sprouts  beans  beef  beef bouillon  \
0             0.0       0.0           0.0    0.0   0.0            0.0   
1             0.0       0.0           0.0    0.0   0.0            0.0   
2             0.0       0.0           0.0    0.0   0.0            0.0   
3             0.0       0.0           0.0    0.0   0.0            0.0   
4             0.0       0.0           0.0    0.0   0.0            0.0   

   beef broth  beef chuck  beef consomm  beef flavor  beef round  \
0         0.0         0.0           0.0          0.0         0.0   
1         0.0         0.0           0.0          0.0         0.0   
2         0.0         0.0           0.0          0.0         0.0   
3         0.0         0.0           0.0          0.0         0.0   
4         0.0         0.0           0.0          0.0         0.0   

   beef shoulder roast  beef stock  beer  beet juice  b

### Sauce group

In [55]:
factor2['sauce'] = factor2['barbecue']+factor2['barbecue sauce']+factor2['bottle ketchup']+factor2['catsup']+factor2['chunky salsa']+ factor2['del monte']+ factor2['dressing']+factor2['dry hidden valley']+factor2['dry hidden valley ranch dressing']+factor2['enchilada sauce']+factor2['french dressing']+ factor2['guacamole dip']+ factor2['guacamole mix']+factor2['herb dressing']+factor2['hot sauce']+factor2['italian cooking sauce']+ factor2['italian dressing']+ factor2['italian salad dressing']+factor2['ketchup']+factor2['low-fat mayonnaise']+factor2['mayo']+factor2['mayonnaise']+ factor2['mustard']+ factor2['picante sauce']+factor2['prepared mustard']+factor2['regular mustard']+factor2['salad crunchies']+factor2['salad dressing']+ factor2['salsa']+ factor2['sauce']+factor2['shrimp sauce']+factor2['soy sauce']+factor2['spaghetti sauce']+factor2['tabasco']+factor2['tabasco sauce']+factor2['teriyaki sauce']+factor2['tomato ketchup']+factor2['tomato sauce']+factor2['unsweetened applesauce']+factor2['worcester sauce']+ factor2['worcestershire']+ factor2['worcestershire sauce']+factor2['yellow mustard']+factor2['your favorite barbecue sauce']+factor2['chili sauce']

In [56]:
sauce_columns_list = ['barbecue','barbecue sauce','bottle ketchup','catsup','chunky salsa','del monte','dressing','dry hidden valley','dry hidden valley ranch dressing','enchilada sauce','french dressing','guacamole dip','guacamole mix','herb dressing','hot sauce','italian cooking sauce','italian dressing','italian salad dressing','ketchup','low-fat mayonnaise','mayo','mayonnaise','mustard','picante sauce','prepared mustard','regular mustard','salad crunchies','salad dressing','salsa','shrimp sauce','soy sauce','spaghetti sauce','tabasco','tabasco sauce','teriyaki sauce','tomato ketchup','tomato sauce','unsweetened applesauce','worcester sauce','worcestershire','worcestershire sauce','yellow mustard','your favorite barbecue sauce','chili sauce']
len(sauce_columns_list)

44

In [57]:
factor2 = factor2.drop(sauce_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 748)


item  active dry yeast  \
0  [pinto beans, cooking oil, catsup, worcestersh...               0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...               0.0   
2  [chicken, cream of chicken, margarine, flour, ...               0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...               0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...               0.0   

   all-purpose  all-purpose flour  almond  almond extract  almond flavoring  \
0          0.0                0.0     0.0             0.0               0.0   
1          0.0                0.0     0.0             0.0               0.0   
2          0.0                0.0     0.0             0.0               0.0   
3          0.0                0.0     0.0             0.0               0.0   
4          0.0                0.0     0.0             0.0               0.0   

   almonds  american cheese  angel  angel food cake  apple  apple cider  \
0      0.0              0.0    0.0              0.0    0.0          0.0   
1      0.0              0.0    0.0              0.0    0.0          0.0   
2      0.0              0.0    0.0              0.0    0.0          0.0   
3      0.0              0.0    0.0              0.0    0.0          0.0   
4      0.0              0.0    0.0              0.0    0.0          0.0   

   apple juice  apple pie filling  apple wedges  apples  applesauce  \
0          0.0                0.0           0.0     0.0         0.0   
1          0.0                0.0           0.0     0.0         0.0   
2          0.0                0.0           0.0     0.0         0.0   
3          0.0                0.0           0.0     0.0         0.0   
4          0.0                0.0           0.0     0.0         0.0   

   baby shrimp  bacon  bacon bits  bacon drippings  bacon grease  \
0          0.0    0.0         0.0              0.0           0.0   
1          0.0    0.0         0.0              0.0           0.0   
2          0.0    0.0         0.0              0.0           0.0   
3          0.0    0.0         0.0              0.0           0.0   
4          0.0    0.0         0.0              0.0           0.0   

   bacon strips  baking apples  baking chocolate  baking mix  baking potatoes  \
0           0.0            0.0               0.0         0.0              0.0   
1           0.0            0.0               0.0         0.0              0.0   
2           0.0            0.0               0.0         0.0              0.0   
3           0.0            0.0               0.0         0.0              0.0   
4           0.0            0.0               0.0         0.0              0.0   

   baking powder  baking soda  bakon slices  balsamic vinegar  bean dip  \
0            0.0          0.0           0.0               0.0       0.0   
1            0.0          0.0           0.0               0.0       0.0   
2            0.0          0.0           0.0               0.0       0.0   
3            0.0          0.0           0.0               0.0       0.0   
4            0.0          0.0           0.0               0.0       0.0   

   bean sprouts  beans  beef  beef bouillon  beef broth  beef chuck  \
0           0.0    0.0   0.0            0.0         0.0         0.0   
1           0.0    0.0   0.0            0.0         0.0         0.0   
2           0.0    0.0   0.0            0.0         0.0         0.0   
3           0.0    0.0   0.0            0.0         0.0         0.0   
4           0.0    0.0   0.0            0.0         0.0         0.0   

   beef consomm  beef flavor  beef round  beef shoulder roast  beef stock  \
0           0.0          0.0         0.0                  0.0         0.0   
1           0.0          0.0         0.0                  0.0         0.0   
2           0.0          0.0         0.0                  0.0         0.0   
3           0.0          0.0         0.0                  0.0         0.0   
4           0.0          0.0         0.0                  0.0         0.0   

   beer  beet

### Cheese Group

In [58]:
factor2['cheese'] = factor2['american cheese']+factor2['cheddar cheese']+factor2['cheese']+factor2['cheese slice']+factor2['cheese slices']+ factor2['cheese strips']+ factor2['colby cheese']+factor2['cool whip']+factor2['cottage cheese']+factor2['cream']+factor2['cream cheese']+ factor2['cubed cheese']+ factor2['english cheese spread']+factor2['freshly grated parmesan cheese']+factor2['frozen cheese blintzes']+factor2['grated cheese']+ factor2['havarti cheese']+ factor2['heavy cream']+factor2['jack cheese']+factor2['light cream']+factor2['mascarpone cheese']+factor2['mostaccioli']+ factor2['mozzarella']+ factor2['mozzarella cheese']+factor2['nonfat sour cream']+factor2['parmesan']+factor2['parmesan cheese']+factor2['philadelphia cream cheese']+ factor2['provolone cheese']+ factor2['ricotta cheese']+factor2['sharp cheese']+factor2['shredded cheese']+factor2['shredded monterey']+factor2['shredded monterey jack cheese']+factor2['shredded mozzarella']+factor2['sour cream']+factor2['swiss cheese']+factor2['tortellini with parmesan cheese']+factor2['velveeta cheese']+factor2['longhorn cheese']

In [59]:
cheese_columns_list = ['american cheese','cheddar cheese','cheese slice','cheese slices','cheese strips','colby cheese','cool whip','cottage cheese','cream','cream cheese','cubed cheese','english cheese spread','freshly grated parmesan cheese','frozen cheese blintzes','grated cheese','havarti cheese','heavy cream','jack cheese','light cream','mascarpone cheese','mostaccioli','mozzarella','mozzarella cheese','nonfat sour cream','parmesan','parmesan cheese','philadelphia cream cheese','provolone cheese','ricotta cheese','sharp cheese','shredded cheese','shredded monterey','shredded monterey jack cheese','shredded mozzarella','sour cream','swiss cheese','tortellini with parmesan cheese','velveeta cheese','longhorn cheese']
len(cheese_columns_list)

39

In [60]:
factor2 = factor2.drop(cheese_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 709)


item  active dry yeast  \
0  [pinto beans, cooking oil, catsup, worcestersh...               0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...               0.0   
2  [chicken, cream of chicken, margarine, flour, ...               0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...               0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...               0.0   

   all-purpose  all-purpose flour  almond  almond extract  almond flavoring  \
0          0.0                0.0     0.0             0.0               0.0   
1          0.0                0.0     0.0             0.0               0.0   
2          0.0                0.0     0.0             0.0               0.0   
3          0.0                0.0     0.0             0.0               0.0   
4          0.0                0.0     0.0             0.0               0.0   

   almonds  angel  angel food cake  apple  apple cider  apple juice  \
0      0.0    0.0              0.0    0.0          0.0          0.0   
1      0.0    0.0              0.0    0.0          0.0          0.0   
2      0.0    0.0              0.0    0.0          0.0          0.0   
3      0.0    0.0              0.0    0.0          0.0          0.0   
4      0.0    0.0              0.0    0.0          0.0          0.0   

   apple pie filling  apple wedges  apples  applesauce  baby shrimp  bacon  \
0                0.0           0.0     0.0         0.0          0.0    0.0   
1                0.0           0.0     0.0         0.0          0.0    0.0   
2                0.0           0.0     0.0         0.0          0.0    0.0   
3                0.0           0.0     0.0         0.0          0.0    0.0   
4                0.0           0.0     0.0         0.0          0.0    0.0   

   bacon bits  bacon drippings  bacon grease  bacon strips  baking apples  \
0         0.0              0.0           0.0           0.0            0.0   
1         0.0              0.0           0.0           0.0            0.0   
2         0.0              0.0           0.0           0.0            0.0   
3         0.0              0.0           0.0           0.0            0.0   
4         0.0              0.0           0.0           0.0            0.0   

   baking chocolate  baking mix  baking potatoes  baking powder  baking soda  \
0               0.0         0.0              0.0            0.0          0.0   
1               0.0         0.0              0.0            0.0          0.0   
2               0.0         0.0              0.0            0.0          0.0   
3               0.0         0.0              0.0            0.0          0.0   
4               0.0         0.0              0.0            0.0          0.0   

   bakon slices  balsamic vinegar  bean dip  bean sprouts  beans  beef  \
0           0.0               0.0       0.0           0.0    0.0   0.0   
1           0.0               0.0       0.0           0.0    0.0   0.0   
2           0.0               0.0       0.0           0.0    0.0   0.0   
3           0.0               0.0       0.0           0.0    0.0   0.0   
4           0.0               0.0       0.0           0.0    0.0   0.0   

   beef bouillon  beef broth  beef chuck  beef consomm  beef flavor  \
0            0.0         0.0         0.0           0.0          0.0   
1            0.0         0.0         0.0           0.0          0.0   
2            0.0         0.0         0.0           0.0          0.0   
3            0.0         0.0         0.0           0.0          0.0   
4            0.0         0.0         0.0           0.0          0.0   

   beef round  beef shoulder roast  beef stock  beer  beet juice  bell pepper  \
0         0.0                  0.0         0.0   0.0         0.0          0.0   
1         0.0                  0.0         0.0   0.0         0.0          0.0   
2         0.0                  0.0         0.0   0.0         0.0          0.0   
3         0.0                  0.0         0.0   0.0         0.0          0.0   
4         0

### Chocolate Group

In [61]:
factor2['chocolate'] = factor2['baking chocolate']+factor2['chocolate']+factor2['chocolate bark']+factor2['chocolate bars']+factor2['chocolate bits']+factor2['chocolate chip cookies']+factor2['chocolate chips']+factor2['chocolate frosting']+factor2['chocolate instant pudding']+factor2['chocolate kisses']+factor2['chocolate mix']+factor2['chocolate pie crust']+factor2['chocolate powder']+factor2['chocolate pudding']+factor2['chocolate syrup']+factor2['cocoa']+factor2['coffee']+factor2['coffee cream']+factor2['coffee creamer']+factor2['coffee granuales']+factor2['dipping chocolate']+ factor2['espresso']+ factor2['instant coffee']+factor2['powdered cocoa']+factor2['semi sweet chocolate chips']+factor2['semi-sweet chocolate']+factor2['semi-sweet chocolate bits']+factor2['semi-sweet chocolate chips']+factor2['semi-sweet chocolate morsels']+factor2['semi-sweet chocolate pieces']+factor2['semi-sweet real chocolate chips']+factor2['sprinkling of chocolate sprinkles']+factor2['sprinkling of chocolate sprinkles']+factor2['swiss chocolate cake mix']+factor2['unsweetened chocolate']+factor2['unsweetened chocolate squares']+factor2['white baking chocolate']+factor2['white chocolate']+factor2['white chocolate chips']

In [62]:
choco_columns_list = ['baking chocolate','chocolate bark','chocolate bars','chocolate bits','chocolate chip cookies','chocolate chips','chocolate frosting','chocolate instant pudding','chocolate kisses','chocolate mix','chocolate pie crust','chocolate powder','chocolate pudding','chocolate syrup','cocoa','coffee','coffee cream','coffee creamer','coffee granuales','dipping chocolate','espresso','instant coffee','powdered cocoa','semi sweet chocolate chips','semi-sweet chocolate','semi-sweet chocolate bits','semi-sweet chocolate chips','semi-sweet chocolate morsels','semi-sweet chocolate pieces','semi-sweet real chocolate chips','sprinkling of chocolate sprinkles','sprinkling of chocolate sprinkles','swiss chocolate cake mix','unsweetened chocolate','unsweetened chocolate squares','white baking chocolate','white chocolate','white chocolate chips']
len(choco_columns_list)

38

In [63]:
factor2 = factor2.drop(choco_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 672)


item  active dry yeast  \
0  [pinto beans, cooking oil, catsup, worcestersh...               0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...               0.0   
2  [chicken, cream of chicken, margarine, flour, ...               0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...               0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...               0.0   

   all-purpose  all-purpose flour  almond  almond extract  almond flavoring  \
0          0.0                0.0     0.0             0.0               0.0   
1          0.0                0.0     0.0             0.0               0.0   
2          0.0                0.0     0.0             0.0               0.0   
3          0.0                0.0     0.0             0.0               0.0   
4          0.0                0.0     0.0             0.0               0.0   

   almonds  angel  angel food cake  apple  apple cider  apple juice  \
0      0.0    0.0              0.0    0.0          0.0          0.0   
1      0.0    0.0              0.0    0.0          0.0          0.0   
2      0.0    0.0              0.0    0.0          0.0          0.0   
3      0.0    0.0              0.0    0.0          0.0          0.0   
4      0.0    0.0              0.0    0.0          0.0          0.0   

   apple pie filling  apple wedges  apples  applesauce  baby shrimp  bacon  \
0                0.0           0.0     0.0         0.0          0.0    0.0   
1                0.0           0.0     0.0         0.0          0.0    0.0   
2                0.0           0.0     0.0         0.0          0.0    0.0   
3                0.0           0.0     0.0         0.0          0.0    0.0   
4                0.0           0.0     0.0         0.0          0.0    0.0   

   bacon bits  bacon drippings  bacon grease  bacon strips  baking apples  \
0         0.0              0.0           0.0           0.0            0.0   
1         0.0              0.0           0.0           0.0            0.0   
2         0.0              0.0           0.0           0.0            0.0   
3         0.0              0.0           0.0           0.0            0.0   
4         0.0              0.0           0.0           0.0            0.0   

   baking mix  baking potatoes  baking powder  baking soda  bakon slices  \
0         0.0              0.0            0.0          0.0           0.0   
1         0.0              0.0            0.0          0.0           0.0   
2         0.0              0.0            0.0          0.0           0.0   
3         0.0              0.0            0.0          0.0           0.0   
4         0.0              0.0            0.0          0.0           0.0   

   balsamic vinegar  bean dip  bean sprouts  beans  beef  beef bouillon  \
0               0.0       0.0           0.0    0.0   0.0            0.0   
1               0.0       0.0           0.0    0.0   0.0            0.0   
2               0.0       0.0           0.0    0.0   0.0            0.0   
3               0.0       0.0           0.0    0.0   0.0            0.0   
4               0.0       0.0           0.0    0.0   0.0            0.0   

   beef broth  beef chuck  beef consomm  beef flavor  beef round  \
0         0.0         0.0           0.0          0.0         0.0   
1         0.0         0.0           0.0          0.0         0.0   
2         0.0         0.0           0.0          0.0         0.0   
3         0.0         0.0           0.0          0.0         0.0   
4         0.0         0.0           0.0          0.0         0.0   

   beef shoulder roast  beef stock  beer  beet juice  bell pepper  \
0                  0.0         0.0   0.0         0.0          0.0   
1                  0.0         0.0   0.0         0.0          0.0   
2                  0.0         0.0   0.0         0.0          0.0   
3                  0.0         0.0   0.0         0.0          0.0   
4                  0.0         0.0   0.0         0.0          0.0   

   bell peppers  biscuit baking mix  

### Condiment Group

In [64]:
factor2['condiment'] = factor2['clove garlic']+factor2['cocktail onions']+factor2['crystallized ginger']+factor2['dry mustard']+factor2['fresh garlic']+factor2['fresh ginger']+factor2['fresh green onions']+factor2['garlic']+factor2['garlic powder']+factor2['garlic salt']+factor2['ginger']+factor2['green onion']+factor2['green onions']+factor2['ground ginger']+factor2['ground mustard']+factor2['onion']+factor2['onion gravy mix']+factor2['onion powder']+factor2['onion salt']+factor2['onions']+factor2['purple onion']+ factor2['red onion']+ factor2['rolls garlic']+factor2['shallots']+factor2['sweet onion']+factor2['toes garlic']+factor2['vanilla']+factor2['vanilla extract']+factor2['vanilla flavoring']+factor2['vanilla frosting supreme']+factor2['vanilla instant pudding']+factor2['vanilla pie filling']+factor2['vanilla pudding']+factor2['vanilla wafer crumbs']+factor2['vanilla wafers']+factor2['white onion']+factor2['white onions']+factor2['yellow onion']+factor2['yellow onions']

In [65]:
condi_columns_list = ['clove garlic','cocktail onions','crystallized ginger','dry mustard','fresh garlic','fresh ginger','fresh green onions','garlic','garlic powder','garlic salt','ginger','green onion','green onions','ground ginger','ground mustard','onion','onion gravy mix','onion powder','onion salt','onions','purple onion','red onion','rolls garlic','shallots','sweet onion','toes garlic','vanilla','vanilla extract','vanilla flavoring','vanilla frosting supreme','vanilla instant pudding','vanilla pie filling','vanilla pudding','vanilla wafer crumbs','vanilla wafers','white onion','white onions','yellow onion','yellow onions']
len(condi_columns_list)

39

In [66]:
factor2 = factor2.drop(condi_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 634)


item  active dry yeast  \
0  [pinto beans, cooking oil, catsup, worcestersh...               0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...               0.0   
2  [chicken, cream of chicken, margarine, flour, ...               0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...               0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...               0.0   

   all-purpose  all-purpose flour  almond  almond extract  almond flavoring  \
0          0.0                0.0     0.0             0.0               0.0   
1          0.0                0.0     0.0             0.0               0.0   
2          0.0                0.0     0.0             0.0               0.0   
3          0.0                0.0     0.0             0.0               0.0   
4          0.0                0.0     0.0             0.0               0.0   

   almonds  angel  angel food cake  apple  apple cider  apple juice  \
0      0.0    0.0              0.0    0.0          0.0          0.0   
1      0.0    0.0              0.0    0.0          0.0          0.0   
2      0.0    0.0              0.0    0.0          0.0          0.0   
3      0.0    0.0              0.0    0.0          0.0          0.0   
4      0.0    0.0              0.0    0.0          0.0          0.0   

   apple pie filling  apple wedges  apples  applesauce  baby shrimp  bacon  \
0                0.0           0.0     0.0         0.0          0.0    0.0   
1                0.0           0.0     0.0         0.0          0.0    0.0   
2                0.0           0.0     0.0         0.0          0.0    0.0   
3                0.0           0.0     0.0         0.0          0.0    0.0   
4                0.0           0.0     0.0         0.0          0.0    0.0   

   bacon bits  bacon drippings  bacon grease  bacon strips  baking apples  \
0         0.0              0.0           0.0           0.0            0.0   
1         0.0              0.0           0.0           0.0            0.0   
2         0.0              0.0           0.0           0.0            0.0   
3         0.0              0.0           0.0           0.0            0.0   
4         0.0              0.0           0.0           0.0            0.0   

   baking mix  baking potatoes  baking powder  baking soda  bakon slices  \
0         0.0              0.0            0.0          0.0           0.0   
1         0.0              0.0            0.0          0.0           0.0   
2         0.0              0.0            0.0          0.0           0.0   
3         0.0              0.0            0.0          0.0           0.0   
4         0.0              0.0            0.0          0.0           0.0   

   balsamic vinegar  bean dip  bean sprouts  beans  beef  beef bouillon  \
0               0.0       0.0           0.0    0.0   0.0            0.0   
1               0.0       0.0           0.0    0.0   0.0            0.0   
2               0.0       0.0           0.0    0.0   0.0            0.0   
3               0.0       0.0           0.0    0.0   0.0            0.0   
4               0.0       0.0           0.0    0.0   0.0            0.0   

   beef broth  beef chuck  beef consomm  beef flavor  beef round  \
0         0.0         0.0           0.0          0.0         0.0   
1         0.0         0.0           0.0          0.0         0.0   
2         0.0         0.0           0.0          0.0         0.0   
3         0.0         0.0           0.0          0.0         0.0   
4         0.0         0.0           0.0          0.0         0.0   

   beef shoulder roast  beef stock  beer  beet juice  bell pepper  \
0                  0.0         0.0   0.0         0.0          0.0   
1                  0.0         0.0   0.0         0.0          0.0   
2                  0.0         0.0   0.0         0.0          0.0   
3                  0.0         0.0   0.0         0.0          0.0   
4                  0.0         0.0   0.0         0.0          0.0   

   bell peppers  biscuit baking mix  

### Meat group

In [67]:
factor2['meat'] = factor2['bacon']+factor2['bacon bits']+factor2['bacon drippings']+factor2['bacon grease']+factor2['bacon strips']+factor2['bakon slices']+factor2['bulk sausage']+factor2['calves liver']+factor2['cold turkey']+factor2['country sausage']+factor2['deli ham']+factor2['duck']+factor2['fully cooked ham']+factor2['ground raw turkey']+factor2['ground smoked ham']+factor2['ground turkey']+factor2['ham']+factor2['ham bone']+factor2['ham broth']+factor2['hard salami']+factor2['hot dogs']+factor2['hot sausage']+factor2['italian sausage']+factor2['lamb breast']+factor2['pepperoni']+factor2['pepperoni slices']+factor2['salami']+factor2['sausage']+factor2['sausages']+factor2['scallions']+factor2['scallops']+factor2['turkey']+factor2['veal']

In [68]:
meat_columns_list = ['bacon','bacon bits','bacon drippings','bacon grease','bacon strips','bakon slices','bulk sausage','calves liver','cold turkey','country sausage','deli ham','duck','fully cooked ham','ground raw turkey','ground smoked ham','ground turkey','ham','ham bone','ham broth','hard salami','hot dogs','hot sausage','italian sausage','lamb breast','pepperoni','pepperoni slices','salami','sausage','sausages','scallions','scallops','turkey','veal']
len(meat_columns_list)

33

In [69]:
factor2 = factor2.drop(meat_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 601)


item  active dry yeast  \
0  [pinto beans, cooking oil, catsup, worcestersh...               0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...               0.0   
2  [chicken, cream of chicken, margarine, flour, ...               0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...               0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...               0.0   

   all-purpose  all-purpose flour  almond  almond extract  almond flavoring  \
0          0.0                0.0     0.0             0.0               0.0   
1          0.0                0.0     0.0             0.0               0.0   
2          0.0                0.0     0.0             0.0               0.0   
3          0.0                0.0     0.0             0.0               0.0   
4          0.0                0.0     0.0             0.0               0.0   

   almonds  angel  angel food cake  apple  apple cider  apple juice  \
0      0.0    0.0              0.0    0.0          0.0          0.0   
1      0.0    0.0              0.0    0.0          0.0          0.0   
2      0.0    0.0              0.0    0.0          0.0          0.0   
3      0.0    0.0              0.0    0.0          0.0          0.0   
4      0.0    0.0              0.0    0.0          0.0          0.0   

   apple pie filling  apple wedges  apples  applesauce  baby shrimp  \
0                0.0           0.0     0.0         0.0          0.0   
1                0.0           0.0     0.0         0.0          0.0   
2                0.0           0.0     0.0         0.0          0.0   
3                0.0           0.0     0.0         0.0          0.0   
4                0.0           0.0     0.0         0.0          0.0   

   baking apples  baking mix  baking potatoes  baking powder  baking soda  \
0            0.0         0.0              0.0            0.0          0.0   
1            0.0         0.0              0.0            0.0          0.0   
2            0.0         0.0              0.0            0.0          0.0   
3            0.0         0.0              0.0            0.0          0.0   
4            0.0         0.0              0.0            0.0          0.0   

   balsamic vinegar  bean dip  bean sprouts  beans  beef  beef bouillon  \
0               0.0       0.0           0.0    0.0   0.0            0.0   
1               0.0       0.0           0.0    0.0   0.0            0.0   
2               0.0       0.0           0.0    0.0   0.0            0.0   
3               0.0       0.0           0.0    0.0   0.0            0.0   
4               0.0       0.0           0.0    0.0   0.0            0.0   

   beef broth  beef chuck  beef consomm  beef flavor  beef round  \
0         0.0         0.0           0.0          0.0         0.0   
1         0.0         0.0           0.0          0.0         0.0   
2         0.0         0.0           0.0          0.0         0.0   
3         0.0         0.0           0.0          0.0         0.0   
4         0.0         0.0           0.0          0.0         0.0   

   beef shoulder roast  beef stock  beer  beet juice  bell pepper  \
0                  0.0         0.0   0.0         0.0          0.0   
1                  0.0         0.0   0.0         0.0          0.0   
2                  0.0         0.0   0.0         0.0          0.0   
3                  0.0         0.0   0.0         0.0          0.0   
4                  0.0         0.0   0.0         0.0          0.0   

   bell peppers  biscuit baking mix  biscuit mix  bisquick  \
0           0.0                 0.0          0.0       0.0   
1           0.0                 0.0          0.0       0.0   
2           0.0                 0.0          0.0       0.0   
3           0.0                 0.0          0.0       0.0   
4           0.0                 0.0          0.0       0.0   

   bisquick baking mix  bisquick mix  black beans  black olives  black pepper  \
0                  0.0           0.0          0.0           0.0           0.0   
1

### Beef Group

In [70]:
factor2['beef'] = factor2['beef']+factor2['beef bouillon']+factor2['beef broth']+factor2['beef chuck']+factor2['beef consomm']+factor2['beef flavor']+factor2['beef round']+factor2['beef shoulder roast']+factor2['beef stock']+factor2['brisket']+factor2['chipped beef']+factor2['clear beef']+factor2['deer meat']+factor2['extra lean ground beef']+factor2['flank steak']+factor2['good beef']+factor2['ground allspice']+factor2['ground beef']+factor2['ground beef patties']+factor2['ground chuck']+factor2['ground chuck beef']+factor2['ground meat']+factor2['lean chili ground beef']+factor2['lean ground beef']+factor2['lean stew meat']+factor2['lean tender beef']+factor2['meat']+factor2['steak']+factor2['stew beef']+factor2['stew meat']+factor2['stewing beef']

In [71]:
beef_columns_list = ['beef bouillon','beef broth','beef chuck','beef consomm','beef flavor','beef round','beef shoulder roast','beef stock','brisket','chipped beef','clear beef','deer meat','extra lean ground beef','flank steak','good beef','ground allspice','ground beef','ground beef patties','ground chuck','ground chuck beef','ground meat','lean chili ground beef','lean ground beef','lean stew meat','lean tender beef','meat','steak','stew beef','stew meat','stewing beef']
len(beef_columns_list)

30

In [72]:
factor2 = factor2.drop(beef_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 571)


item  active dry yeast  \
0  [pinto beans, cooking oil, catsup, worcestersh...               0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...               0.0   
2  [chicken, cream of chicken, margarine, flour, ...               0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...               0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...               0.0   

   all-purpose  all-purpose flour  almond  almond extract  almond flavoring  \
0          0.0                0.0     0.0             0.0               0.0   
1          0.0                0.0     0.0             0.0               0.0   
2          0.0                0.0     0.0             0.0               0.0   
3          0.0                0.0     0.0             0.0               0.0   
4          0.0                0.0     0.0             0.0               0.0   

   almonds  angel  angel food cake  apple  apple cider  apple juice  \
0      0.0    0.0              0.0    0.0          0.0          0.0   
1      0.0    0.0              0.0    0.0          0.0          0.0   
2      0.0    0.0              0.0    0.0          0.0          0.0   
3      0.0    0.0              0.0    0.0          0.0          0.0   
4      0.0    0.0              0.0    0.0          0.0          0.0   

   apple pie filling  apple wedges  apples  applesauce  baby shrimp  \
0                0.0           0.0     0.0         0.0          0.0   
1                0.0           0.0     0.0         0.0          0.0   
2                0.0           0.0     0.0         0.0          0.0   
3                0.0           0.0     0.0         0.0          0.0   
4                0.0           0.0     0.0         0.0          0.0   

   baking apples  baking mix  baking potatoes  baking powder  baking soda  \
0            0.0         0.0              0.0            0.0          0.0   
1            0.0         0.0              0.0            0.0          0.0   
2            0.0         0.0              0.0            0.0          0.0   
3            0.0         0.0              0.0            0.0          0.0   
4            0.0         0.0              0.0            0.0          0.0   

   balsamic vinegar  bean dip  bean sprouts  beans  beef  beer  beet juice  \
0               0.0       0.0           0.0    0.0   0.0   0.0         0.0   
1               0.0       0.0           0.0    0.0   0.0   0.0         0.0   
2               0.0       0.0           0.0    0.0   0.0   0.0         0.0   
3               0.0       0.0           0.0    0.0   0.0   0.0         0.0   
4               0.0       0.0           0.0    0.0   0.0   0.0         0.0   

   bell pepper  bell peppers  biscuit baking mix  biscuit mix  bisquick  \
0          0.0           0.0                 0.0          0.0       0.0   
1          0.0           0.0                 0.0          0.0       0.0   
2          0.0           0.0                 0.0          0.0       0.0   
3          0.0           0.0                 0.0          0.0       0.0   
4          0.0           0.0                 0.0          0.0       0.0   

   bisquick baking mix  bisquick mix  black beans  black olives  black pepper  \
0                  0.0           0.0          0.0           0.0           0.0   
1                  0.0           0.0          0.0           0.0           0.0   
2                  0.0           0.0          0.0           0.0           0.0   
3                  0.0           0.0          0.0           0.0           0.0   
4                  0.0           0.0          0.0           0.0           0.0   

   black peppercorns  black walnuts  black-eyed peas  boiling water  \
0                0.0            0.0              0.0            0.0   
1                0.0            0.0              0.0            0.0   
2                0.0            0.0              0.0            0.0   
3                0.0            0.0              0.0            0.0   
4                0.0            0.0              

### Flour Group

In [73]:
factor2['flour'] = factor2['active dry yeast']+factor2['all-purpose']+factor2['all-purpose flour']+factor2['baking mix']+factor2['baking powder']+factor2['baking soda']+factor2['bisquick']+factor2['bisquick baking mix']+factor2['bisquick mix']+factor2['caramel topping']+factor2['cornbread mix']+factor2['cornmeal']+factor2['cornstarch']+factor2['curry powder']+factor2['double acting baking powder']+factor2['flour']+factor2['flour tortilla']+factor2['flour tortillas']+factor2['flour/water']+factor2['pancake mix']+factor2['tapioca']+factor2['unbleached white flour']+factor2['white flour']+factor2['whole wheat flour']+factor2['yeast']+factor2['yellow cake']+factor2['yellow cake mix']

In [74]:
flour_columns_list = ['active dry yeast','all-purpose',"all-purpose flour",'baking mix','baking powder','baking soda','bisquick','bisquick baking mix','bisquick mix','caramel topping','cornbread mix','cornmeal','cornstarch','curry powder','double acting baking powder','flour tortilla','flour tortillas','flour/water','pancake mix','tapioca','unbleached white flour','white flour','whole wheat flour','yeast','yellow cake','yellow cake mix']
len(flour_columns_list)

26

In [75]:
factor2 = factor2.drop(flour_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 545)


item  almond  almond extract  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0             0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0             0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0             0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     0.0             0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0             0.0   

   almond flavoring  almonds  angel  angel food cake  apple  apple cider  \
0               0.0      0.0    0.0              0.0    0.0          0.0   
1               0.0      0.0    0.0              0.0    0.0          0.0   
2               0.0      0.0    0.0              0.0    0.0          0.0   
3               0.0      0.0    0.0              0.0    0.0          0.0   
4               0.0      0.0    0.0              0.0    0.0          0.0   

   apple juice  apple pie filling  apple wedges  apples  applesauce  \
0          0.0                0.0           0.0     0.0         0.0   
1          0.0                0.0           0.0     0.0         0.0   
2          0.0                0.0           0.0     0.0         0.0   
3          0.0                0.0           0.0     0.0         0.0   
4          0.0                0.0           0.0     0.0         0.0   

   baby shrimp  baking apples  baking potatoes  balsamic vinegar  bean dip  \
0          0.0            0.0              0.0               0.0       0.0   
1          0.0            0.0              0.0               0.0       0.0   
2          0.0            0.0              0.0               0.0       0.0   
3          0.0            0.0              0.0               0.0       0.0   
4          0.0            0.0              0.0               0.0       0.0   

   bean sprouts  beans  beef  beer  beet juice  bell pepper  bell peppers  \
0           0.0    0.0   0.0   0.0         0.0          0.0           0.0   
1           0.0    0.0   0.0   0.0         0.0          0.0           0.0   
2           0.0    0.0   0.0   0.0         0.0          0.0           0.0   
3           0.0    0.0   0.0   0.0         0.0          0.0           0.0   
4           0.0    0.0   0.0   0.0         0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black beans  black olives  black pepper  \
0                 0.0          0.0          0.0           0.0           0.0   
1                 0.0          0.0          0.0           0.0           0.0   
2                 0.0          0.0          0.0           0.0           0.0   
3                 0.0          0.0          0.0           0.0           0.0   
4                 0.0          0.0          0.0           0.0           0.0   

   black peppercorns  black walnuts  black-eyed peas  boiling water  \
0                0.0            0.0              0.0            0.0   
1                0.0            0.0              0.0            0.0   
2                0.0            0.0              0.0            0.0   
3                0.0            0.0              0.0            0.0   
4                0.0            0.0              0.0            0.0   

   boneless chicken  boneless skinless chicken breast  bourbon  brandy  bread  \
0               0.0                               0.0      0.0     0.0    0.0   
1               0.0                               0.0      0.0     0.0    0.0   
2               0.0                               0.0      0.0     0.0    0.0   
3               0.0                               0.0      0.0     0.0    0.0   
4               0.0                               0.0      0.0     0.0    0.0   

   bread croutons  bread crumbs  bread cubes  \
0             0.0           0.0          0.0   
1             0.0           0.0          0.0   
2             0.0           0.0          0.0   
3             0.0           0.0          0.0   
4             0.0           0.0          0.0   

   breyers golden vanilla ice cream  broiler-fryer chicken  brown  \
0   

### Liquid Group

In [76]:
factor2['liquid'] = factor2['apple juice']+factor2['beet juice']+factor2['boiling water']+factor2['certo']+factor2['cold half and half']+factor2['cold tap water']+factor2['cold water']+factor2['corn syrup']+factor2['cranberry juice cocktail']+factor2['garbanzo water']+factor2['garbanzo water']+factor2['hot water']+factor2['light corn syrup']+factor2['light karo syrup']+factor2['maple flavoring']+factor2['maple syrup']+factor2['pickle juice']+factor2['pickle lime']+factor2['pickle relish']+factor2['pineapple juice']+factor2['squash']+factor2['syrup']+factor2['warm water']+factor2['water']+factor2['white corn syrup']+factor2['white karo syrup']+factor2['white syrup']+factor2['grape juice']

In [77]:
liquid_columns_list = ['apple juice','beet juice','boiling water','certo','cold half and half','cold tap water','cold water','corn syrup','cranberry juice cocktail','garbanzo water','garbanzo water','grape juice','hot water','light corn syrup','light karo syrup','maple flavoring','maple syrup','pickle juice','pickle lime','pickle relish','pineapple juice','squash','syrup','warm water','water','white corn syrup','white karo syrup','white syrup']
len(liquid_columns_list)

28

In [78]:
factor2 = factor2.drop(liquid_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 519)


item  almond  almond extract  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0             0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0             0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0             0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     0.0             0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0             0.0   

   almond flavoring  almonds  angel  angel food cake  apple  apple cider  \
0               0.0      0.0    0.0              0.0    0.0          0.0   
1               0.0      0.0    0.0              0.0    0.0          0.0   
2               0.0      0.0    0.0              0.0    0.0          0.0   
3               0.0      0.0    0.0              0.0    0.0          0.0   
4               0.0      0.0    0.0              0.0    0.0          0.0   

   apple pie filling  apple wedges  apples  applesauce  baby shrimp  \
0                0.0           0.0     0.0         0.0          0.0   
1                0.0           0.0     0.0         0.0          0.0   
2                0.0           0.0     0.0         0.0          0.0   
3                0.0           0.0     0.0         0.0          0.0   
4                0.0           0.0     0.0         0.0          0.0   

   baking apples  baking potatoes  balsamic vinegar  bean dip  bean sprouts  \
0            0.0              0.0               0.0       0.0           0.0   
1            0.0              0.0               0.0       0.0           0.0   
2            0.0              0.0               0.0       0.0           0.0   
3            0.0              0.0               0.0       0.0           0.0   
4            0.0              0.0               0.0       0.0           0.0   

   beans  beef  beer  bell pepper  bell peppers  biscuit baking mix  \
0    0.0   0.0   0.0          0.0           0.0                 0.0   
1    0.0   0.0   0.0          0.0           0.0                 0.0   
2    0.0   0.0   0.0          0.0           0.0                 0.0   
3    0.0   0.0   0.0          0.0           0.0                 0.0   
4    0.0   0.0   0.0          0.0           0.0                 0.0   

   biscuit mix  black beans  black olives  black pepper  black peppercorns  \
0          0.0          0.0           0.0           0.0                0.0   
1          0.0          0.0           0.0           0.0                0.0   
2          0.0          0.0           0.0           0.0                0.0   
3          0.0          0.0           0.0           0.0                0.0   
4          0.0          0.0           0.0           0.0                0.0   

   black walnuts  black-eyed peas  boneless chicken  \
0            0.0              0.0               0.0   
1            0.0              0.0               0.0   
2            0.0              0.0               0.0   
3            0.0              0.0               0.0   
4            0.0              0.0               0.0   

   boneless skinless chicken breast  bourbon  brandy  bread  bread croutons  \
0                               0.0      0.0     0.0    0.0             0.0   
1                               0.0      0.0     0.0    0.0             0.0   
2                               0.0      0.0     0.0    0.0             0.0   
3                               0.0      0.0     0.0    0.0             0.0   
4                               0.0      0.0     0.0    0.0             0.0   

   bread crumbs  bread cubes  breyers golden vanilla ice cream  \
0           0.0          0.0                               0.0   
1           0.0          0.0                               0.0   
2           0.0          0.0                               0.0   
3           0.0          0.0                               0.0   
4           0.0          0.0                               0.0   

   broiler-fryer chicken  brown  brown potatoes  brown rice  brown sugar  \
0                    0.0    0.0  

### Cake Mix group

In [79]:
factor2['cake_mix'] = factor2['brownie mix']+factor2['cake']+factor2['cake cubes']+factor2['cake flour']+factor2['cake mix']+factor2['cake yeast']+factor2['cakes']+factor2['crescent dinner rolls']+factor2['crescent roll']+factor2['crescent rolls']+factor2['gelatin']+factor2['gelatine']+factor2['instant chocolate pudding']+factor2['instant vanilla pudding']+factor2['instant vanilla pudding mix']+factor2['instant vanilla/chocolate pudding']+factor2['jello']+factor2['pineapple cake mix']+factor2['pistachio pudding']+factor2['pretzel crumbs']+factor2['pretzel rods']+factor2['pretzels']+factor2['pudding']+factor2['pudding included yellow cake mix']+factor2['red jello']+factor2['tart pie cherries']

In [80]:
cake_columns_list = ['brownie mix','cake','cake cubes','cake flour','cake mix','cake yeast','cakes','crescent dinner rolls','crescent roll','crescent rolls','gelatin','gelatine','instant chocolate pudding','instant vanilla pudding','instant vanilla pudding mix','instant vanilla/chocolate pudding','jello','pineapple cake mix','pistachio pudding','pretzel crumbs','pretzel rods','pretzels','pudding','pudding included yellow cake mix','red jello','tart pie cherries']
len(cake_columns_list)

26

In [81]:
factor2 = factor2.drop(cake_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 494)


item  almond  almond extract  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0             0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0             0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0             0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     0.0             0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0             0.0   

   almond flavoring  almonds  angel  angel food cake  apple  apple cider  \
0               0.0      0.0    0.0              0.0    0.0          0.0   
1               0.0      0.0    0.0              0.0    0.0          0.0   
2               0.0      0.0    0.0              0.0    0.0          0.0   
3               0.0      0.0    0.0              0.0    0.0          0.0   
4               0.0      0.0    0.0              0.0    0.0          0.0   

   apple pie filling  apple wedges  apples  applesauce  baby shrimp  \
0                0.0           0.0     0.0         0.0          0.0   
1                0.0           0.0     0.0         0.0          0.0   
2                0.0           0.0     0.0         0.0          0.0   
3                0.0           0.0     0.0         0.0          0.0   
4                0.0           0.0     0.0         0.0          0.0   

   baking apples  baking potatoes  balsamic vinegar  bean dip  bean sprouts  \
0            0.0              0.0               0.0       0.0           0.0   
1            0.0              0.0               0.0       0.0           0.0   
2            0.0              0.0               0.0       0.0           0.0   
3            0.0              0.0               0.0       0.0           0.0   
4            0.0              0.0               0.0       0.0           0.0   

   beans  beef  beer  bell pepper  bell peppers  biscuit baking mix  \
0    0.0   0.0   0.0          0.0           0.0                 0.0   
1    0.0   0.0   0.0          0.0           0.0                 0.0   
2    0.0   0.0   0.0          0.0           0.0                 0.0   
3    0.0   0.0   0.0          0.0           0.0                 0.0   
4    0.0   0.0   0.0          0.0           0.0                 0.0   

   biscuit mix  black beans  black olives  black pepper  black peppercorns  \
0          0.0          0.0           0.0           0.0                0.0   
1          0.0          0.0           0.0           0.0                0.0   
2          0.0          0.0           0.0           0.0                0.0   
3          0.0          0.0           0.0           0.0                0.0   
4          0.0          0.0           0.0           0.0                0.0   

   black walnuts  black-eyed peas  boneless chicken  \
0            0.0              0.0               0.0   
1            0.0              0.0               0.0   
2            0.0              0.0               0.0   
3            0.0              0.0               0.0   
4            0.0              0.0               0.0   

   boneless skinless chicken breast  bourbon  brandy  bread  bread croutons  \
0                               0.0      0.0     0.0    0.0             0.0   
1                               0.0      0.0     0.0    0.0             0.0   
2                               0.0      0.0     0.0    0.0             0.0   
3                               0.0      0.0     0.0    0.0             0.0   
4                               0.0      0.0     0.0    0.0             0.0   

   bread crumbs  bread cubes  breyers golden vanilla ice cream  \
0           0.0          0.0                               0.0   
1           0.0          0.0                               0.0   
2           0.0          0.0                               0.0   
3           0.0          0.0                               0.0   
4           0.0          0.0                               0.0   

   broiler-fryer chicken  brown  brown potatoes  brown rice  brown sugar  \
0                    0.0    0.0  

### NUTS Groups

In [82]:
factor2['nuts'] = factor2['almonds']+factor2['almond']+factor2['almond extract']+factor2['almond flavoring']+factor2['almond']+factor2['black walnuts']+factor2['california walnuts']+factor2['chachere cajun']+factor2['chopped walnut meats']+factor2['chunky peanut butter']+factor2['crunchy peanut butter']+factor2['ground pecans']+factor2['ground walnuts']+factor2['homemade peanut butter']+factor2['nuts']+factor2['peanut butter']+factor2['peanuts']+factor2['pecan']+factor2['pecan chips']+factor2['pecan halves']+factor2['pecans']+factor2['slivered almonds']+factor2['walnut pieces']+factor2['walnuts']

In [83]:
nuts_columns_list = ['almonds','almond','almond extract','almond flavoring','almond','black walnuts','california walnuts','chachere cajun','chopped walnut meats','chunky peanut butter','crunchy peanut butter','ground pecans','ground walnuts','homemade peanut butter','peanut butter','peanuts','pecan','pecan chips','pecan halves','pecans','slivered almonds','walnut pieces','walnuts']
len(nuts_columns_list)

23

In [84]:
factor2 = factor2.drop(nuts_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 472)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baby shrimp  baking apples  baking potatoes  balsamic vinegar  bean dip  \
0          0.0            0.0              0.0               0.0       0.0   
1          0.0            0.0              0.0               0.0       0.0   
2          0.0            0.0              0.0               0.0       0.0   
3          0.0            0.0              0.0               0.0       0.0   
4          0.0            0.0              0.0               0.0       0.0   

   bean sprouts  beans  beef  beer  bell pepper  bell peppers  \
0           0.0    0.0   0.0   0.0          0.0           0.0   
1           0.0    0.0   0.0   0.0          0.0           0.0   
2           0.0    0.0   0.0   0.0          0.0           0.0   
3           0.0    0.0   0.0   0.0          0.0           0.0   
4           0.0    0.0   0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black beans  black olives  black pepper  \
0                 0.0          0.0          0.0           0.0           0.0   
1                 0.0          0.0          0.0           0.0           0.0   
2                 0.0          0.0          0.0           0.0           0.0   
3                 0.0          0.0          0.0           0.0           0.0   
4                 0.0          0.0          0.0           0.0           0.0   

   black peppercorns  black-eyed peas  boneless chicken  \
0                0.0              0.0               0.0   
1                0.0              0.0               0.0   
2                0.0              0.0               0.0   
3                0.0              0.0               0.0   
4                0.0              0.0               0.0   

   boneless skinless chicken breast  bourbon  brandy  bread  bread croutons  \
0                               0.0      0.0     0.0    0.0             0.0   
1                               0.0      0.0     0.0    0.0             0.0   
2                               0.0      0.0     0.0    0.0             0.0   
3                               0.0      0.0     0.0    0.0             0.0   
4                               0.0      0.0     0.0    0.0             0.0   

   bread crumbs  bread cubes  breyers golden vanilla ice cream  \
0           0.0          0.0                               0.0   
1           0.0          0.0                               0.0   
2           0.0          0.0                               0.0   
3           0.0          0.0                               0.0   
4           0.0          0.0                               0.0   

   broiler-fryer chicken  brown  brown potatoes  brown rice  brown sugar  \
0                    0.0    0.0             0.0         0.0          1.0   
1                    0.0    0.0             0.0         0.0          0.0   
2                    0.0    0.0             0.0         0.0          0.0   
3                    0.0    0.0             0.0         0.0          0.0   
4                    0.0    0.0             0.0         0.0          0.0   

   butter  butter beans  buttered bread crumbs  butterfinger  buttermilk  \
0  

### Lemon groups

In [85]:
factor2['lemon'] = factor2['frozen lemonade']+factor2['lemon']+factor2['lemon extract']+factor2['lemon flavored gelatin']+factor2['lemon flavoring']+factor2['lemon jello']+factor2['lemon juice']+factor2['lemon juice from']+factor2['lemon pepper']+factor2['lemon pie filling']+factor2['lemon pudding']+factor2['lemon rind']+factor2['lemon yogurt']+factor2['lemon-lime']+factor2['lemonade']+factor2['lemons']+factor2['lime']+factor2['lime jello']+factor2['lime juice']+factor2['lime juice concentrate']+factor2['lime sherbet']+factor2['limes']+factor2['pink lemonade']

In [86]:
lemon_columns_list = ['frozen lemonade','lemon extract','lemon flavored gelatin','lemon flavoring','lemon jello','lemon juice','lemon juice from','lemon pepper','lemon pie filling','lemon pudding','lemon rind','lemon yogurt','lemon-lime','lemonade','lemons','lime','lime jello','lime juice','lime juice concentrate','lime sherbet','limes','pink lemonade']
len(lemon_columns_list)

22

In [87]:
factor2 = factor2.drop(lemon_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 450)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baby shrimp  baking apples  baking potatoes  balsamic vinegar  bean dip  \
0          0.0            0.0              0.0               0.0       0.0   
1          0.0            0.0              0.0               0.0       0.0   
2          0.0            0.0              0.0               0.0       0.0   
3          0.0            0.0              0.0               0.0       0.0   
4          0.0            0.0              0.0               0.0       0.0   

   bean sprouts  beans  beef  beer  bell pepper  bell peppers  \
0           0.0    0.0   0.0   0.0          0.0           0.0   
1           0.0    0.0   0.0   0.0          0.0           0.0   
2           0.0    0.0   0.0   0.0          0.0           0.0   
3           0.0    0.0   0.0   0.0          0.0           0.0   
4           0.0    0.0   0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black beans  black olives  black pepper  \
0                 0.0          0.0          0.0           0.0           0.0   
1                 0.0          0.0          0.0           0.0           0.0   
2                 0.0          0.0          0.0           0.0           0.0   
3                 0.0          0.0          0.0           0.0           0.0   
4                 0.0          0.0          0.0           0.0           0.0   

   black peppercorns  black-eyed peas  boneless chicken  \
0                0.0              0.0               0.0   
1                0.0              0.0               0.0   
2                0.0              0.0               0.0   
3                0.0              0.0               0.0   
4                0.0              0.0               0.0   

   boneless skinless chicken breast  bourbon  brandy  bread  bread croutons  \
0                               0.0      0.0     0.0    0.0             0.0   
1                               0.0      0.0     0.0    0.0             0.0   
2                               0.0      0.0     0.0    0.0             0.0   
3                               0.0      0.0     0.0    0.0             0.0   
4                               0.0      0.0     0.0    0.0             0.0   

   bread crumbs  bread cubes  breyers golden vanilla ice cream  \
0           0.0          0.0                               0.0   
1           0.0          0.0                               0.0   
2           0.0          0.0                               0.0   
3           0.0          0.0                               0.0   
4           0.0          0.0                               0.0   

   broiler-fryer chicken  brown  brown potatoes  brown rice  brown sugar  \
0                    0.0    0.0             0.0         0.0          1.0   
1                    0.0    0.0             0.0         0.0          0.0   
2                    0.0    0.0             0.0         0.0          0.0   
3                    0.0    0.0             0.0         0.0          0.0   
4                    0.0    0.0             0.0         0.0          0.0   

   butter  butter beans  buttered bread crumbs  butterfinger  buttermilk  \
0  

### Pepper Group

In [88]:
factor2['pepper'] = factor2['black pepper']+factor2['black peppercorns']+factor2['cayenne']+factor2['coarse black pepper']+factor2['fresh ground pepper']+factor2['freshly ground pepper']+factor2['green chili peppers']+factor2['green pepper']+factor2['green peppers']+factor2['ground black pepper']+factor2['ground pepper']+factor2['ground red pepper']+factor2['hot green pepper']+factor2['hot pepper']+factor2['hot peppers']+factor2['jalapeno pepper']+factor2['jalapeno peppers']+factor2['pepper']+factor2['peppercorns']+factor2['pepperoncini salad peppers']+factor2['peppers']+factor2['white pepper']+factor2['cayenne pepper']

In [89]:
pepper_columns_list = ['black pepper','black peppercorns','cayenne','cayenne pepper','coarse black pepper','fresh ground pepper','freshly ground pepper','green chili peppers','green pepper','green peppers','ground black pepper','ground pepper','ground red pepper','hot green pepper','hot pepper','hot peppers','jalapeno pepper','jalapeno peppers','peppercorns','pepperoncini salad peppers','peppers','white pepper']
len(pepper_columns_list)

22

In [90]:
factor2 = factor2.drop(pepper_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 428)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baby shrimp  baking apples  baking potatoes  balsamic vinegar  bean dip  \
0          0.0            0.0              0.0               0.0       0.0   
1          0.0            0.0              0.0               0.0       0.0   
2          0.0            0.0              0.0               0.0       0.0   
3          0.0            0.0              0.0               0.0       0.0   
4          0.0            0.0              0.0               0.0       0.0   

   bean sprouts  beans  beef  beer  bell pepper  bell peppers  \
0           0.0    0.0   0.0   0.0          0.0           0.0   
1           0.0    0.0   0.0   0.0          0.0           0.0   
2           0.0    0.0   0.0   0.0          0.0           0.0   
3           0.0    0.0   0.0   0.0          0.0           0.0   
4           0.0    0.0   0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black beans  black olives  \
0                 0.0          0.0          0.0           0.0   
1                 0.0          0.0          0.0           0.0   
2                 0.0          0.0          0.0           0.0   
3                 0.0          0.0          0.0           0.0   
4                 0.0          0.0          0.0           0.0   

   black-eyed peas  boneless chicken  boneless skinless chicken breast  \
0              0.0               0.0                               0.0   
1              0.0               0.0                               0.0   
2              0.0               0.0                               0.0   
3              0.0               0.0                               0.0   
4              0.0               0.0                               0.0   

   bourbon  brandy  bread  bread croutons  bread crumbs  bread cubes  \
0      0.0     0.0    0.0             0.0           0.0          0.0   
1      0.0     0.0    0.0             0.0           0.0          0.0   
2      0.0     0.0    0.0             0.0           0.0          0.0   
3      0.0     0.0    0.0             0.0           0.0          0.0   
4      0.0     0.0    0.0             0.0           0.0          0.0   

   breyers golden vanilla ice cream  broiler-fryer chicken  brown  \
0                               0.0                    0.0    0.0   
1                               0.0                    0.0    0.0   
2                               0.0                    0.0    0.0   
3                               0.0                    0.0    0.0   
4                               0.0                    0.0    0.0   

   brown potatoes  brown rice  brown sugar  butter  butter beans  \
0             0.0         0.0          1.0     0.0           0.0   
1             0.0         0.0          0.0     0.0           0.0   
2             0.0         0.0          0.0     0.0           0.0   
3             0.0         0.0          0.0     0.0           0.0   
4             0.0         0.0          0.0     1.0           0.0   

   buttered bread crumbs  butterfinger  buttermilk  buttermilk baking mix  \
0                    0.0           0.0         0.0                  

### Soup Group

In [91]:
factor2['soup'] = factor2['campbell']+factor2["campbell's cream"]+factor2["campbell's tomato soup"]+factor2['celery soup']+factor2['cream of asparagus soup']+factor2['cream of celery soup']+factor2['cream of chicken soup']+factor2['cream of mushroom soup']+factor2['cream of mushroom soup undiluted']+factor2['cream of potato soup']+factor2['cream of shrimp soup']+factor2['cream of tomato soup']+factor2['creamy soup']+factor2['golden mushroom soup']+factor2['knorr swiss vegetable soup']+factor2['mushroom soup']+factor2['onion soup']+factor2['onion soup mix']+factor2['tomato soup']+factor2['vegetable soup']

In [92]:
soup_columns_list = ['campbell',"campbell's cream","campbell's tomato soup",'celery soup','cream of asparagus soup','cream of celery soup','cream of chicken soup','cream of mushroom soup','cream of mushroom soup undiluted','cream of potato soup','cream of shrimp soup','cream of tomato soup','creamy soup','golden mushroom soup','knorr swiss vegetable soup','mushroom soup','onion soup','onion soup mix','tomato soup','vegetable soup']
len(soup_columns_list)

20

In [93]:
factor2 = factor2.drop(soup_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 409)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baby shrimp  baking apples  baking potatoes  balsamic vinegar  bean dip  \
0          0.0            0.0              0.0               0.0       0.0   
1          0.0            0.0              0.0               0.0       0.0   
2          0.0            0.0              0.0               0.0       0.0   
3          0.0            0.0              0.0               0.0       0.0   
4          0.0            0.0              0.0               0.0       0.0   

   bean sprouts  beans  beef  beer  bell pepper  bell peppers  \
0           0.0    0.0   0.0   0.0          0.0           0.0   
1           0.0    0.0   0.0   0.0          0.0           0.0   
2           0.0    0.0   0.0   0.0          0.0           0.0   
3           0.0    0.0   0.0   0.0          0.0           0.0   
4           0.0    0.0   0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black beans  black olives  \
0                 0.0          0.0          0.0           0.0   
1                 0.0          0.0          0.0           0.0   
2                 0.0          0.0          0.0           0.0   
3                 0.0          0.0          0.0           0.0   
4                 0.0          0.0          0.0           0.0   

   black-eyed peas  boneless chicken  boneless skinless chicken breast  \
0              0.0               0.0                               0.0   
1              0.0               0.0                               0.0   
2              0.0               0.0                               0.0   
3              0.0               0.0                               0.0   
4              0.0               0.0                               0.0   

   bourbon  brandy  bread  bread croutons  bread crumbs  bread cubes  \
0      0.0     0.0    0.0             0.0           0.0          0.0   
1      0.0     0.0    0.0             0.0           0.0          0.0   
2      0.0     0.0    0.0             0.0           0.0          0.0   
3      0.0     0.0    0.0             0.0           0.0          0.0   
4      0.0     0.0    0.0             0.0           0.0          0.0   

   breyers golden vanilla ice cream  broiler-fryer chicken  brown  \
0                               0.0                    0.0    0.0   
1                               0.0                    0.0    0.0   
2                               0.0                    0.0    0.0   
3                               0.0                    0.0    0.0   
4                               0.0                    0.0    0.0   

   brown potatoes  brown rice  brown sugar  butter  butter beans  \
0             0.0         0.0          1.0     0.0           0.0   
1             0.0         0.0          0.0     0.0           0.0   
2             0.0         0.0          0.0     0.0           0.0   
3             0.0         0.0          0.0     0.0           0.0   
4             0.0         0.0          0.0     1.0           0.0   

   buttered bread crumbs  butterfinger  buttermilk  buttermilk baking mix  \
0                    0.0           0.0         0.0                  

### Oil-vinager group

In [94]:
factor2['oil_vinegar'] = factor2['balsamic vinegar']+factor2['canola oil']+factor2['choice']+factor2['cider vinegar']+factor2['cooking oil']+factor2['crisco']+factor2['crisco oil']+factor2['italian olive oil']+factor2['light oil']+factor2['oil']+factor2['olive oil']+factor2['rice vinegar']+factor2['salad oil']+factor2['sesame oil']+factor2['tarragon vinegar']+factor2['vegetable oil']+factor2['vinegar']+factor2['wesson oil']+factor2['white balsamic vinegar']+factor2['white vinegar']

In [95]:
oil_columns_list = ['balsamic vinegar','canola oil','choice','cider vinegar','cooking oil','crisco','crisco oil','italian olive oil','light oil','oil','olive oil','rice vinegar','salad oil','sesame oil','tarragon vinegar','vegetable oil','vinegar','wesson oil','white balsamic vinegar','white vinegar']
len(oil_columns_list)

20

In [96]:
factor2 = factor2.drop(oil_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 390)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baby shrimp  baking apples  baking potatoes  bean dip  bean sprouts  beans  \
0          0.0            0.0              0.0       0.0           0.0    0.0   
1          0.0            0.0              0.0       0.0           0.0    0.0   
2          0.0            0.0              0.0       0.0           0.0    0.0   
3          0.0            0.0              0.0       0.0           0.0    0.0   
4          0.0            0.0              0.0       0.0           0.0    0.0   

   beef  beer  bell pepper  bell peppers  biscuit baking mix  biscuit mix  \
0   0.0   0.0          0.0           0.0                 0.0          0.0   
1   0.0   0.0          0.0           0.0                 0.0          0.0   
2   0.0   0.0          0.0           0.0                 0.0          0.0   
3   0.0   0.0          0.0           0.0                 0.0          0.0   
4   0.0   0.0          0.0           0.0                 0.0          0.0   

   black beans  black olives  black-eyed peas  boneless chicken  \
0          0.0           0.0              0.0               0.0   
1          0.0           0.0              0.0               0.0   
2          0.0           0.0              0.0               0.0   
3          0.0           0.0              0.0               0.0   
4          0.0           0.0              0.0               0.0   

   boneless skinless chicken breast  bourbon  brandy  bread  bread croutons  \
0                               0.0      0.0     0.0    0.0             0.0   
1                               0.0      0.0     0.0    0.0             0.0   
2                               0.0      0.0     0.0    0.0             0.0   
3                               0.0      0.0     0.0    0.0             0.0   
4                               0.0      0.0     0.0    0.0             0.0   

   bread crumbs  bread cubes  breyers golden vanilla ice cream  \
0           0.0          0.0                               0.0   
1           0.0          0.0                               0.0   
2           0.0          0.0                               0.0   
3           0.0          0.0                               0.0   
4           0.0          0.0                               0.0   

   broiler-fryer chicken  brown  brown potatoes  brown rice  brown sugar  \
0                    0.0    0.0             0.0         0.0          1.0   
1                    0.0    0.0             0.0         0.0          0.0   
2                    0.0    0.0             0.0         0.0          0.0   
3                    0.0    0.0             0.0         0.0          0.0   
4                    0.0    0.0             0.0         0.0          0.0   

   butter  butter beans  buttered bread crumbs  butterfinger  buttermilk  \
0     0.0           0.0                    0.0           0.0         0.0   
1     0.0           0.0                    0.0           0.0         0.0   
2     0.0           0.0                    0.0           0.0         1.0   
3     0.0           0.0                    0.0           0.0         0.0   
4     1.0           0.0             

### Milk Group

In [97]:
factor2['milk'] = factor2['c.milk']+factor2['carnation']+factor2['carnation milk']+factor2['cold milk']+factor2['condensed milk']+factor2['condensed cream']+factor2['fresh goat milk']+factor2['hot milk']+factor2['low-fat milk']+factor2['magnolia condensed milk']+factor2['milk']+factor2['milk chocolate']+factor2['milk chocolate bar']+factor2['milk chocolate chips']+factor2['milk chocolate frosting']+factor2['nonfat dry milk']+factor2['pet milk']+factor2['powdered milk']+factor2['sour milk']+factor2['sweet milk']

In [98]:
milk_columns_list = ['c.milk','carnation','carnation milk','cold milk','condensed milk','condensed cream','fresh goat milk','hot milk','low-fat milk','magnolia condensed milk','milk chocolate','milk chocolate bar','milk chocolate chips','milk chocolate frosting','nonfat dry milk','pet milk','powdered milk','sour milk','sweet milk']
len(milk_columns_list)

19

In [99]:
factor2 = factor2.drop(milk_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 371)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baby shrimp  baking apples  baking potatoes  bean dip  bean sprouts  beans  \
0          0.0            0.0              0.0       0.0           0.0    0.0   
1          0.0            0.0              0.0       0.0           0.0    0.0   
2          0.0            0.0              0.0       0.0           0.0    0.0   
3          0.0            0.0              0.0       0.0           0.0    0.0   
4          0.0            0.0              0.0       0.0           0.0    0.0   

   beef  beer  bell pepper  bell peppers  biscuit baking mix  biscuit mix  \
0   0.0   0.0          0.0           0.0                 0.0          0.0   
1   0.0   0.0          0.0           0.0                 0.0          0.0   
2   0.0   0.0          0.0           0.0                 0.0          0.0   
3   0.0   0.0          0.0           0.0                 0.0          0.0   
4   0.0   0.0          0.0           0.0                 0.0          0.0   

   black beans  black olives  black-eyed peas  boneless chicken  \
0          0.0           0.0              0.0               0.0   
1          0.0           0.0              0.0               0.0   
2          0.0           0.0              0.0               0.0   
3          0.0           0.0              0.0               0.0   
4          0.0           0.0              0.0               0.0   

   boneless skinless chicken breast  bourbon  brandy  bread  bread croutons  \
0                               0.0      0.0     0.0    0.0             0.0   
1                               0.0      0.0     0.0    0.0             0.0   
2                               0.0      0.0     0.0    0.0             0.0   
3                               0.0      0.0     0.0    0.0             0.0   
4                               0.0      0.0     0.0    0.0             0.0   

   bread crumbs  bread cubes  breyers golden vanilla ice cream  \
0           0.0          0.0                               0.0   
1           0.0          0.0                               0.0   
2           0.0          0.0                               0.0   
3           0.0          0.0                               0.0   
4           0.0          0.0                               0.0   

   broiler-fryer chicken  brown  brown potatoes  brown rice  brown sugar  \
0                    0.0    0.0             0.0         0.0          1.0   
1                    0.0    0.0             0.0         0.0          0.0   
2                    0.0    0.0             0.0         0.0          0.0   
3                    0.0    0.0             0.0         0.0          0.0   
4                    0.0    0.0             0.0         0.0          0.0   

   butter  butter beans  buttered bread crumbs  butterfinger  buttermilk  \
0     0.0           0.0                    0.0           0.0         0.0   
1     0.0           0.0                    0.0           0.0         0.0   
2     0.0           0.0                    0.0           0.0         1.0   
3     0.0           0.0                    0.0           0.0         0.0   
4     1.0           0.0             

### Fish Group

In [100]:
factor2['fish'] = factor2['baby shrimp']+factor2['clams']+factor2['crab meat']+factor2['crabmeat']+factor2['crawfish tails']+factor2['fresh lump crabmeat']+factor2['fresh shrimp']+factor2['frozen crabmeat']+factor2['haddock fillets']+factor2['imitation crabmeat']+factor2['lean fish']+factor2['lobster']+factor2['salmon']+factor2['salmon fillet']+factor2['shrimp']+factor2['tiny shrimp']+factor2['tuna']+factor2['white crabmeat']+factor2['white fish']

In [101]:
fish_columns_list = ['baby shrimp','clams','crab meat','crabmeat','crawfish tails','fresh lump crabmeat','fresh shrimp','frozen crabmeat','haddock fillets','imitation crabmeat','lean fish','lobster','salmon','salmon fillet','shrimp','tiny shrimp','tuna','white crabmeat','white fish']
len(fish_columns_list)

19

In [102]:
factor2 = factor2.drop(fish_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 353)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baking apples  baking potatoes  bean dip  bean sprouts  beans  beef  beer  \
0            0.0              0.0       0.0           0.0    0.0   0.0   0.0   
1            0.0              0.0       0.0           0.0    0.0   0.0   0.0   
2            0.0              0.0       0.0           0.0    0.0   0.0   0.0   
3            0.0              0.0       0.0           0.0    0.0   0.0   0.0   
4            0.0              0.0       0.0           0.0    0.0   0.0   0.0   

   bell pepper  bell peppers  biscuit baking mix  biscuit mix  black beans  \
0          0.0           0.0                 0.0          0.0          0.0   
1          0.0           0.0                 0.0          0.0          0.0   
2          0.0           0.0                 0.0          0.0          0.0   
3          0.0           0.0                 0.0          0.0          0.0   
4          0.0           0.0                 0.0          0.0          0.0   

   black olives  black-eyed peas  boneless chicken  \
0           0.0              0.0               0.0   
1           0.0              0.0               0.0   
2           0.0              0.0               0.0   
3           0.0              0.0               0.0   
4           0.0              0.0               0.0   

   boneless skinless chicken breast  bourbon  brandy  bread  bread croutons  \
0                               0.0      0.0     0.0    0.0             0.0   
1                               0.0      0.0     0.0    0.0             0.0   
2                               0.0      0.0     0.0    0.0             0.0   
3                               0.0      0.0     0.0    0.0             0.0   
4                               0.0      0.0     0.0    0.0             0.0   

   bread crumbs  bread cubes  breyers golden vanilla ice cream  \
0           0.0          0.0                               0.0   
1           0.0          0.0                               0.0   
2           0.0          0.0                               0.0   
3           0.0          0.0                               0.0   
4           0.0          0.0                               0.0   

   broiler-fryer chicken  brown  brown potatoes  brown rice  brown sugar  \
0                    0.0    0.0             0.0         0.0          1.0   
1                    0.0    0.0             0.0         0.0          0.0   
2                    0.0    0.0             0.0         0.0          0.0   
3                    0.0    0.0             0.0         0.0          0.0   
4                    0.0    0.0             0.0         0.0          0.0   

   butter  butter beans  buttered bread crumbs  butterfinger  buttermilk  \
0     0.0           0.0                    0.0           0.0         0.0   
1     0.0           0.0                    0.0           0.0         0.0   
2     0.0           0.0                    0.0           0.0         1.0   
3     0.0           0.0                    0.0           0.0         0.0   
4     1.0           0.0                    0.0           0.0         0.0   

   buttermilk baking mix  butterscotc

### Chicken Group

In [103]:
factor2['chicken'] = factor2['boneless chicken']+factor2['boneless chicken']+factor2['broiler-fryer chicken']+factor2['chicken']+factor2['chicken bouillon']+factor2['chicken breast']+factor2['chicken breasts']+factor2['chicken broth']+factor2['chicken cutlets']+factor2['chicken flavored bouillon granules']+factor2['chicken flavored ramen noodles']+factor2['chicken granules']+factor2['chicken gumbo soup']+factor2['chicken mushroom']+factor2['chicken parts']+factor2['chicken stock']+factor2['chunk breast of chicken']+factor2['instant chicken']+factor2['white chicken meat']+factor2['boneless skinless chicken breast']

In [104]:
chicken_columns_list = ['boneless chicken','boneless chicken','broiler-fryer chicken','chicken bouillon','chicken breast','chicken breasts','chicken broth','chicken cutlets','chicken flavored bouillon granules','chicken flavored ramen noodles','chicken granules','chicken gumbo soup','chicken mushroom','chicken parts','chicken stock','chunk breast of chicken','instant chicken','white chicken meat','boneless skinless chicken breast']
len(chicken_columns_list)

19

In [105]:
factor2 = factor2.drop(chicken_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 335)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baking apples  baking potatoes  bean dip  bean sprouts  beans  beef  beer  \
0            0.0              0.0       0.0           0.0    0.0   0.0   0.0   
1            0.0              0.0       0.0           0.0    0.0   0.0   0.0   
2            0.0              0.0       0.0           0.0    0.0   0.0   0.0   
3            0.0              0.0       0.0           0.0    0.0   0.0   0.0   
4            0.0              0.0       0.0           0.0    0.0   0.0   0.0   

   bell pepper  bell peppers  biscuit baking mix  biscuit mix  black beans  \
0          0.0           0.0                 0.0          0.0          0.0   
1          0.0           0.0                 0.0          0.0          0.0   
2          0.0           0.0                 0.0          0.0          0.0   
3          0.0           0.0                 0.0          0.0          0.0   
4          0.0           0.0                 0.0          0.0          0.0   

   black olives  black-eyed peas  bourbon  brandy  bread  bread croutons  \
0           0.0              0.0      0.0     0.0    0.0             0.0   
1           0.0              0.0      0.0     0.0    0.0             0.0   
2           0.0              0.0      0.0     0.0    0.0             0.0   
3           0.0              0.0      0.0     0.0    0.0             0.0   
4           0.0              0.0      0.0     0.0    0.0             0.0   

   bread crumbs  bread cubes  breyers golden vanilla ice cream  brown  \
0           0.0          0.0                               0.0    0.0   
1           0.0          0.0                               0.0    0.0   
2           0.0          0.0                               0.0    0.0   
3           0.0          0.0                               0.0    0.0   
4           0.0          0.0                               0.0    0.0   

   brown potatoes  brown rice  brown sugar  butter  butter beans  \
0             0.0         0.0          1.0     0.0           0.0   
1             0.0         0.0          0.0     0.0           0.0   
2             0.0         0.0          0.0     0.0           0.0   
3             0.0         0.0          0.0     0.0           0.0   
4             0.0         0.0          0.0     1.0           0.0   

   buttered bread crumbs  butterfinger  buttermilk  buttermilk baking mix  \
0                    0.0           0.0         0.0                    0.0   
1                    0.0           0.0         0.0                    0.0   
2                    0.0           0.0         1.0                    0.0   
3                    0.0           0.0         0.0                    0.0   
4                    0.0           0.0         0.0                    0.0   

   butterscotch chips  butterscotch ice cream topping  butterscotch pudding  \
0                 0.0                             0.0                   0.0   
1                 0.0                             0.0                   0.0   
2                 0.0                             0.0                   0.0   
3                 0.0                             0.0           

### Beans groups

In [106]:
factor2['beans'] = factor2['bean dip']+factor2['bean sprouts']+factor2['beans']+factor2['black beans']+factor2['cooked navy beans']+factor2['frozen lima beans']+factor2['garbanzo beans']+factor2['green beans']+factor2['green lima beans']+factor2['italian green beans']+factor2['kidney beans']+factor2['light red kidney beans']+factor2['northern beans']+factor2['pinto beans']+factor2['red beans']+factor2['string beans']+factor2['wax beans']+factor2['yellow beans']

In [107]:
beans_columns_list = ['bean dip','bean sprouts','black beans','cooked navy beans','frozen lima beans','garbanzo beans','green beans','green lima beans','italian green beans','kidney beans','light red kidney beans','northern beans','pinto beans','red beans','string beans','wax beans','yellow beans']
len(beans_columns_list)

17

In [108]:
factor2 = factor2.drop(beans_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 318)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baking apples  baking potatoes  beans  beef  beer  bell pepper  \
0            0.0              0.0    1.0   0.0   0.0          0.0   
1            0.0              0.0    0.0   0.0   0.0          0.0   
2            0.0              0.0    0.0   0.0   0.0          0.0   
3            0.0              0.0    0.0   0.0   0.0          0.0   
4            0.0              0.0    0.0   0.0   0.0          0.0   

   bell peppers  biscuit baking mix  biscuit mix  black olives  \
0           0.0                 0.0          0.0           0.0   
1           0.0                 0.0          0.0           0.0   
2           0.0                 0.0          0.0           0.0   
3           0.0                 0.0          0.0           0.0   
4           0.0                 0.0          0.0           0.0   

   black-eyed peas  bourbon  brandy  bread  bread croutons  bread crumbs  \
0              0.0      0.0     0.0    0.0             0.0           0.0   
1              0.0      0.0     0.0    0.0             0.0           0.0   
2              0.0      0.0     0.0    0.0             0.0           0.0   
3              0.0      0.0     0.0    0.0             0.0           0.0   
4              0.0      0.0     0.0    0.0             0.0           0.0   

   bread cubes  breyers golden vanilla ice cream  brown  brown potatoes  \
0          0.0                               0.0    0.0             0.0   
1          0.0                               0.0    0.0             0.0   
2          0.0                               0.0    0.0             0.0   
3          0.0                               0.0    0.0             0.0   
4          0.0                               0.0    0.0             0.0   

   brown rice  brown sugar  butter  butter beans  buttered bread crumbs  \
0         0.0          1.0     0.0           0.0                    0.0   
1         0.0          0.0     0.0           0.0                    0.0   
2         0.0          0.0     0.0           0.0                    0.0   
3         0.0          0.0     0.0           0.0                    0.0   
4         0.0          0.0     1.0           0.0                    0.0   

   butterfinger  buttermilk  buttermilk baking mix  butterscotch chips  \
0           0.0         0.0                    0.0                 0.0   
1           0.0         0.0                    0.0                 0.0   
2           0.0         1.0                    0.0                 0.0   
3           0.0         0.0                    0.0                 0.0   
4           0.0         0.0                    0.0                 0.0   

   butterscotch ice cream topping  butterscotch pudding  canned applesauce  \
0                             0.0                   0.0                0.0   
1                             0.0                   0.0                0.0   
2                             0.0                   0.0                0.0   
3                             0.0                   0.0                0.0   
4                             0.0                   0.0                0.0   

   castor sug

### Pasta group

In [109]:
factor2['pasta'] = factor2['elbow macaroni']+factor2['fettucine']+factor2['linguine pasta']+factor2['linguini']+factor2['macaroni']+factor2['macaroni shells']+factor2['orzo pasta']+factor2['pasta']+factor2['pasta-style']+factor2['penne pasta']+factor2['rigatoni']+factor2['seashell macaroni']+factor2['shell']+factor2['shell macaroni']+factor2['spaghetti']+factor2['spiral pasta']+factor2['thin spaghetti']+factor2['velveeta shells']

In [110]:
pasta_columns_list = ['elbow macaroni','fettucine','linguine pasta','linguini','macaroni','macaroni shells','orzo pasta','pasta-style','penne pasta','rigatoni','seashell macaroni','shell','shell macaroni','spaghetti','spiral pasta','thin spaghetti','velveeta shells']
len(pasta_columns_list)

17

In [111]:
factor2 = factor2.drop(pasta_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 301)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baking apples  baking potatoes  beans  beef  beer  bell pepper  \
0            0.0              0.0    1.0   0.0   0.0          0.0   
1            0.0              0.0    0.0   0.0   0.0          0.0   
2            0.0              0.0    0.0   0.0   0.0          0.0   
3            0.0              0.0    0.0   0.0   0.0          0.0   
4            0.0              0.0    0.0   0.0   0.0          0.0   

   bell peppers  biscuit baking mix  biscuit mix  black olives  \
0           0.0                 0.0          0.0           0.0   
1           0.0                 0.0          0.0           0.0   
2           0.0                 0.0          0.0           0.0   
3           0.0                 0.0          0.0           0.0   
4           0.0                 0.0          0.0           0.0   

   black-eyed peas  bourbon  brandy  bread  bread croutons  bread crumbs  \
0              0.0      0.0     0.0    0.0             0.0           0.0   
1              0.0      0.0     0.0    0.0             0.0           0.0   
2              0.0      0.0     0.0    0.0             0.0           0.0   
3              0.0      0.0     0.0    0.0             0.0           0.0   
4              0.0      0.0     0.0    0.0             0.0           0.0   

   bread cubes  breyers golden vanilla ice cream  brown  brown potatoes  \
0          0.0                               0.0    0.0             0.0   
1          0.0                               0.0    0.0             0.0   
2          0.0                               0.0    0.0             0.0   
3          0.0                               0.0    0.0             0.0   
4          0.0                               0.0    0.0             0.0   

   brown rice  brown sugar  butter  butter beans  buttered bread crumbs  \
0         0.0          1.0     0.0           0.0                    0.0   
1         0.0          0.0     0.0           0.0                    0.0   
2         0.0          0.0     0.0           0.0                    0.0   
3         0.0          0.0     0.0           0.0                    0.0   
4         0.0          0.0     1.0           0.0                    0.0   

   butterfinger  buttermilk  buttermilk baking mix  butterscotch chips  \
0           0.0         0.0                    0.0                 0.0   
1           0.0         0.0                    0.0                 0.0   
2           0.0         1.0                    0.0                 0.0   
3           0.0         0.0                    0.0                 0.0   
4           0.0         0.0                    0.0                 0.0   

   butterscotch ice cream topping  butterscotch pudding  canned applesauce  \
0                             0.0                   0.0                0.0   
1                             0.0                   0.0                0.0   
2                             0.0                   0.0                0.0   
3                             0.0                   0.0                0.0   
4                             0.0                   0.0                0.0   

   castor sug

### Alcohol group

In [112]:
factor2['alcohol'] = factor2['beer']+factor2['bourbon']+factor2['brandy']+factor2['clam liquor']+factor2['cooking sherry']+factor2['ginger ale']+factor2['ginger root']+factor2['grand marnier']+factor2['kahlua']+factor2['red wine']+factor2['rum']+factor2['rum flavoring']+factor2['vodka']+factor2['whiskey']+factor2['white wine']+factor2['wine']+factor2['wine vinegar']+factor2['your favorite beer']

In [113]:
alcohol_columns_list = ['beer','bourbon','brandy','clam liquor','cooking sherry','ginger ale','ginger root','grand marnier','kahlua','red wine','rum','rum flavoring','vodka','whiskey','white wine','wine','wine vinegar','your favorite beer']
len(alcohol_columns_list)

18

In [114]:
factor2 = factor2.drop(alcohol_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 284)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baking apples  baking potatoes  beans  beef  bell pepper  bell peppers  \
0            0.0              0.0    1.0   0.0          0.0           0.0   
1            0.0              0.0    0.0   0.0          0.0           0.0   
2            0.0              0.0    0.0   0.0          0.0           0.0   
3            0.0              0.0    0.0   0.0          0.0           0.0   
4            0.0              0.0    0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black olives  black-eyed peas  bread  \
0                 0.0          0.0           0.0              0.0    0.0   
1                 0.0          0.0           0.0              0.0    0.0   
2                 0.0          0.0           0.0              0.0    0.0   
3                 0.0          0.0           0.0              0.0    0.0   
4                 0.0          0.0           0.0              0.0    0.0   

   bread croutons  bread crumbs  bread cubes  \
0             0.0           0.0          0.0   
1             0.0           0.0          0.0   
2             0.0           0.0          0.0   
3             0.0           0.0          0.0   
4             0.0           0.0          0.0   

   breyers golden vanilla ice cream  brown  brown potatoes  brown rice  \
0                               0.0    0.0             0.0         0.0   
1                               0.0    0.0             0.0         0.0   
2                               0.0    0.0             0.0         0.0   
3                               0.0    0.0             0.0         0.0   
4                               0.0    0.0             0.0         0.0   

   brown sugar  butter  butter beans  buttered bread crumbs  butterfinger  \
0          1.0     0.0           0.0                    0.0           0.0   
1          0.0     0.0           0.0                    0.0           0.0   
2          0.0     0.0           0.0                    0.0           0.0   
3          0.0     0.0           0.0                    0.0           0.0   
4          0.0     1.0           0.0                    0.0           0.0   

   buttermilk  buttermilk baking mix  butterscotch chips  \
0         0.0                    0.0                 0.0   
1         0.0                    0.0                 0.0   
2         1.0                    0.0                 0.0   
3         0.0                    0.0                 0.0   
4         0.0                    0.0                 0.0   

   butterscotch ice cream topping  butterscotch pudding  canned applesauce  \
0                             0.0                   0.0                0.0   
1                             0.0                   0.0                0.0   
2                             0.0                   0.0                0.0   
3                             0.0                   0.0                0.0   
4                             0.0                   0.0                0.0   

   castor sugar  cereal  cheerios  cheese  chick peas  chicken  chiles  \
0           0.0     0.0       0.0     0.0         0.0      0.0     0.0   
1  

### Butter group

In [115]:
factor2['butter'] = factor2['butter']+factor2['butter beans']+factor2['buttered bread crumbs']+factor2['butterfinger']+factor2['buttermilk']+factor2['buttermilk baking mix']+factor2['butterscotch chips']+factor2['butterscotch ice cream topping']+factor2['butterscotch pudding']+factor2['country butter']+factor2['liquid butter']+factor2['margarine']+factor2['pads margarine']+factor2['parkay margarine']+factor2['sweet butter']+factor2['unsalted butter']+factor2['unsalted margarine']

In [116]:
butter_columns_list = ['butter beans','buttered bread crumbs','butterfinger','buttermilk','buttermilk baking mix','butterscotch chips','butterscotch ice cream topping','butterscotch pudding','country butter','liquid butter','margarine','pads margarine','parkay margarine','sweet butter','unsalted butter','unsalted margarine']
len(butter_columns_list)

16

In [117]:
factor2 = factor2.drop(butter_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 268)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apple  apple cider  apple pie filling  apple wedges  apples  applesauce  \
0    0.0          0.0                0.0           0.0     0.0         0.0   
1    0.0          0.0                0.0           0.0     0.0         0.0   
2    0.0          0.0                0.0           0.0     0.0         0.0   
3    0.0          0.0                0.0           0.0     0.0         0.0   
4    0.0          0.0                0.0           0.0     0.0         0.0   

   baking apples  baking potatoes  beans  beef  bell pepper  bell peppers  \
0            0.0              0.0    1.0   0.0          0.0           0.0   
1            0.0              0.0    0.0   0.0          0.0           0.0   
2            0.0              0.0    0.0   0.0          0.0           0.0   
3            0.0              0.0    0.0   0.0          0.0           0.0   
4            0.0              0.0    0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black olives  black-eyed peas  bread  \
0                 0.0          0.0           0.0              0.0    0.0   
1                 0.0          0.0           0.0              0.0    0.0   
2                 0.0          0.0           0.0              0.0    0.0   
3                 0.0          0.0           0.0              0.0    0.0   
4                 0.0          0.0           0.0              0.0    0.0   

   bread croutons  bread crumbs  bread cubes  \
0             0.0           0.0          0.0   
1             0.0           0.0          0.0   
2             0.0           0.0          0.0   
3             0.0           0.0          0.0   
4             0.0           0.0          0.0   

   breyers golden vanilla ice cream  brown  brown potatoes  brown rice  \
0                               0.0    0.0             0.0         0.0   
1                               0.0    0.0             0.0         0.0   
2                               0.0    0.0             0.0         0.0   
3                               0.0    0.0             0.0         0.0   
4                               0.0    0.0             0.0         0.0   

   brown sugar  butter  canned applesauce  castor sugar  cereal  cheerios  \
0          1.0     0.0                0.0           0.0     0.0       0.0   
1          0.0     0.0                0.0           0.0     0.0       0.0   
2          0.0     2.0                0.0           0.0     0.0       0.0   
3          0.0     0.0                0.0           0.0     0.0       0.0   
4          0.0     1.0                0.0           0.0     0.0       0.0   

   cheese  chick peas  chicken  chiles  chili mix  chili powder  \
0     0.0         0.0      0.0     0.0        0.0           0.0   
1     1.0         0.0      0.0     0.0        0.0           0.0   
2     0.0         0.0      1.0     0.0        0.0           0.0   
3     1.0         0.0      0.0     0.0        0.0           0.0   
4     1.0         0.0      0.0     0.0        0.0           0.0   

   chili with beans  chilli powder  chocolate  chocolate ice cream  coconut  \
0               0.0            0.0        0.0                  0.0      0.0   
1               0.0            0.0        0.0                  0.0      0.0   
2               0.0            0.0        0.0                  0.0      0.0   
3               0.0            0.0        0.0                  0.0      0.0   
4               0.0            0.0        0.0                  0.0      0.0   

   coconut cream  coconut cream filling  coconut extract  coconut flakes  \
0            0.0           

### Apples Group

In [118]:
factor2['apples'] = factor2['apple']+factor2['apple cider']+factor2['apple pie filling']+factor2['apple wedges']+factor2['apples']+factor2['applesauce']+factor2['baking apples']+factor2['canned applesauce']+factor2['cooking apples']+factor2['cooking apples']+factor2['fresh apples']+factor2['golden delicious apples']+factor2['grated apples']+factor2['peeled apples']+factor2['red apples']+factor2['tart apples']+factor2['unpeeled apples']

In [119]:
apples_columns_list = ['apple','apple cider','apple pie filling','apple wedges','applesauce','baking apples','canned applesauce','cooking apples','cooking apples','fresh apples','golden delicious apples','grated apples','peeled apples','red apples','tart apples','unpeeled apples']
len(apples_columns_list)

16

In [120]:
factor2 = factor2.drop(apples_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 253)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  baking potatoes  beans  beef  bell pepper  bell peppers  \
0     0.0              0.0    1.0   0.0          0.0           0.0   
1     0.0              0.0    0.0   0.0          0.0           0.0   
2     0.0              0.0    0.0   0.0          0.0           0.0   
3     1.0              0.0    0.0   0.0          0.0           0.0   
4     0.0              0.0    0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black olives  black-eyed peas  bread  \
0                 0.0          0.0           0.0              0.0    0.0   
1                 0.0          0.0           0.0              0.0    0.0   
2                 0.0          0.0           0.0              0.0    0.0   
3                 0.0          0.0           0.0              0.0    0.0   
4                 0.0          0.0           0.0              0.0    0.0   

   bread croutons  bread crumbs  bread cubes  \
0             0.0           0.0          0.0   
1             0.0           0.0          0.0   
2             0.0           0.0          0.0   
3             0.0           0.0          0.0   
4             0.0           0.0          0.0   

   breyers golden vanilla ice cream  brown  brown potatoes  brown rice  \
0                               0.0    0.0             0.0         0.0   
1                               0.0    0.0             0.0         0.0   
2                               0.0    0.0             0.0         0.0   
3                               0.0    0.0             0.0         0.0   
4                               0.0    0.0             0.0         0.0   

   brown sugar  butter  castor sugar  cereal  cheerios  cheese  chick peas  \
0          1.0     0.0           0.0     0.0       0.0     0.0         0.0   
1          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
2          0.0     2.0           0.0     0.0       0.0     0.0         0.0   
3          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
4          0.0     1.0           0.0     0.0       0.0     1.0         0.0   

   chicken  chiles  chili mix  chili powder  chili with beans  chilli powder  \
0      0.0     0.0        0.0           0.0               0.0            0.0   
1      0.0     0.0        0.0           0.0               0.0            0.0   
2      1.0     0.0        0.0           0.0               0.0            0.0   
3      0.0     0.0        0.0           0.0               0.0            0.0   
4      0.0     0.0        0.0           0.0               0.0            0.0   

   chocolate  chocolate ice cream  coconut  coconut cream  \
0        0.0                  0.0      0.0            0.0   
1        0.0                  0.0      0.0            0.0   
2        0.0                  0.0      0.0            0.0   
3        0.0                  0.0      0.0            0.0   
4        0.0                  0.0      0.0            0.0   

   coconut cream filling  coconut extract  coconut flakes  \
0                    0.0              0.0             0.0   
1                    0.0              0.0             0.0   
2                    0.0              0.0             0.0   
3                    0.0              0.0             0.0   
4                    0.0              0.0             0.0   

   confectioners sugar  cookie crumbs  cookie dough  corn  corn bread  \
0                  0.0            0.0           0.0   0.0         0.0   
1                  0.0            0.0           0.0   0.0         0.0   
2                  0.0            0.0           0.0 

### Orange group

In [121]:
factor2['oranges'] = factor2['mandarin oranges']+factor2['orange']+factor2['orange extract']+factor2['orange gelatin']+factor2['orange jell-o']+factor2['orange jello']+factor2['orange juice']+factor2['orange marmalade']+factor2['orange pop']+factor2['orange rind']+factor2['orange sherbet']+factor2['orange slice candy']+factor2['orange zest']+factor2['orange-flavored gelatin']+factor2['oranges']

In [122]:
oranges_columns_list = ['mandarin oranges','orange','orange extract','orange gelatin','orange jell-o','orange jello','orange juice','orange marmalade','orange pop','orange rind','orange sherbet','orange slice candy','orange zest','orange-flavored gelatin']
len(oranges_columns_list)

14

In [123]:
factor2 = factor2.drop(oranges_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 239)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  baking potatoes  beans  beef  bell pepper  bell peppers  \
0     0.0              0.0    1.0   0.0          0.0           0.0   
1     0.0              0.0    0.0   0.0          0.0           0.0   
2     0.0              0.0    0.0   0.0          0.0           0.0   
3     1.0              0.0    0.0   0.0          0.0           0.0   
4     0.0              0.0    0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black olives  black-eyed peas  bread  \
0                 0.0          0.0           0.0              0.0    0.0   
1                 0.0          0.0           0.0              0.0    0.0   
2                 0.0          0.0           0.0              0.0    0.0   
3                 0.0          0.0           0.0              0.0    0.0   
4                 0.0          0.0           0.0              0.0    0.0   

   bread croutons  bread crumbs  bread cubes  \
0             0.0           0.0          0.0   
1             0.0           0.0          0.0   
2             0.0           0.0          0.0   
3             0.0           0.0          0.0   
4             0.0           0.0          0.0   

   breyers golden vanilla ice cream  brown  brown potatoes  brown rice  \
0                               0.0    0.0             0.0         0.0   
1                               0.0    0.0             0.0         0.0   
2                               0.0    0.0             0.0         0.0   
3                               0.0    0.0             0.0         0.0   
4                               0.0    0.0             0.0         0.0   

   brown sugar  butter  castor sugar  cereal  cheerios  cheese  chick peas  \
0          1.0     0.0           0.0     0.0       0.0     0.0         0.0   
1          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
2          0.0     2.0           0.0     0.0       0.0     0.0         0.0   
3          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
4          0.0     1.0           0.0     0.0       0.0     1.0         0.0   

   chicken  chiles  chili mix  chili powder  chili with beans  chilli powder  \
0      0.0     0.0        0.0           0.0               0.0            0.0   
1      0.0     0.0        0.0           0.0               0.0            0.0   
2      1.0     0.0        0.0           0.0               0.0            0.0   
3      0.0     0.0        0.0           0.0               0.0            0.0   
4      0.0     0.0        0.0           0.0               0.0            0.0   

   chocolate  chocolate ice cream  coconut  coconut cream  \
0        0.0                  0.0      0.0            0.0   
1        0.0                  0.0      0.0            0.0   
2        0.0                  0.0      0.0            0.0   
3        0.0                  0.0      0.0            0.0   
4        0.0                  0.0      0.0            0.0   

   coconut cream filling  coconut extract  coconut flakes  \
0                    0.0              0.0             0.0   
1                    0.0              0.0             0.0   
2                    0.0              0.0             0.0   
3                    0.0              0.0             0.0   
4                    0.0              0.0             0.0   

   confectioners sugar  cookie crumbs  cookie dough  corn  corn bread  \
0                  0.0            0.0           0.0   0.0         0.0   
1                  0.0            0.0           0.0   0.0         0.0   
2                  0.0            0.0           0.0 

### Bread Group

In [124]:
factor2['bread'] = factor2['bread']+factor2['bread croutons']+factor2['bread crumbs']+factor2['bread cubes']+factor2['croutons']+factor2['herb seasoned croutons']+factor2['italian bread']+factor2['italian bread crumbs']+factor2['italian style seasoned bread crumbs']+factor2['italian-seasoned breadcrumbs']+factor2['light bread']+factor2['saltine crumbs']+factor2['shortbread']+factor2['white bread']+factor2['whole wheat bread dough']

In [125]:
bread_columns_list = ['bread croutons','bread crumbs','bread cubes','croutons','herb seasoned croutons','italian bread','italian bread crumbs','italian style seasoned bread crumbs','italian-seasoned breadcrumbs','light bread','saltine crumbs','shortbread','white bread','whole wheat bread dough']
len(bread_columns_list)

14

In [126]:
factor2 = factor2.drop(bread_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 225)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  baking potatoes  beans  beef  bell pepper  bell peppers  \
0     0.0              0.0    1.0   0.0          0.0           0.0   
1     0.0              0.0    0.0   0.0          0.0           0.0   
2     0.0              0.0    0.0   0.0          0.0           0.0   
3     1.0              0.0    0.0   0.0          0.0           0.0   
4     0.0              0.0    0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black olives  black-eyed peas  bread  \
0                 0.0          0.0           0.0              0.0    0.0   
1                 0.0          0.0           0.0              0.0    0.0   
2                 0.0          0.0           0.0              0.0    0.0   
3                 0.0          0.0           0.0              0.0    0.0   
4                 0.0          0.0           0.0              0.0    0.0   

   breyers golden vanilla ice cream  brown  brown potatoes  brown rice  \
0                               0.0    0.0             0.0         0.0   
1                               0.0    0.0             0.0         0.0   
2                               0.0    0.0             0.0         0.0   
3                               0.0    0.0             0.0         0.0   
4                               0.0    0.0             0.0         0.0   

   brown sugar  butter  castor sugar  cereal  cheerios  cheese  chick peas  \
0          1.0     0.0           0.0     0.0       0.0     0.0         0.0   
1          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
2          0.0     2.0           0.0     0.0       0.0     0.0         0.0   
3          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
4          0.0     1.0           0.0     0.0       0.0     1.0         0.0   

   chicken  chiles  chili mix  chili powder  chili with beans  chilli powder  \
0      0.0     0.0        0.0           0.0               0.0            0.0   
1      0.0     0.0        0.0           0.0               0.0            0.0   
2      1.0     0.0        0.0           0.0               0.0            0.0   
3      0.0     0.0        0.0           0.0               0.0            0.0   
4      0.0     0.0        0.0           0.0               0.0            0.0   

   chocolate  chocolate ice cream  coconut  coconut cream  \
0        0.0                  0.0      0.0            0.0   
1        0.0                  0.0      0.0            0.0   
2        0.0                  0.0      0.0            0.0   
3        0.0                  0.0      0.0            0.0   
4        0.0                  0.0      0.0            0.0   

   coconut cream filling  coconut extract  coconut flakes  \
0                    0.0              0.0             0.0   
1                    0.0              0.0             0.0   
2                    0.0              0.0             0.0   
3                    0.0              0.0             0.0   
4                    0.0              0.0             0.0   

   confectioners sugar  cookie crumbs  cookie dough  corn  corn bread  \
0                  0.0            0.0           0.0   0.0         0.0   
1                  0.0            0.0           0.0   0.0         0.0   
2                  0.0            0.0           0.0   0.0         0.0   
3                  0.0            0.0           0.0   0.0         0.0   
4                  0.0            0.0           0.0   0.0         0.0   

   corn chips  corn flakes  corn meal  corn muffin  corn tortillas  \
0         0.0          0.0        0.0          0.0 

### Chili group

In [127]:
factor2['chili'] = factor2['chiles']+factor2['chili mix']+factor2['chili powder']+factor2['chili with beans']+factor2['chilli powder']+factor2['fresh red chili']+factor2['green chilies']+factor2['green chilis']+factor2['pimento']+factor2['pimentos']+factor2['pimiento']+factor2['pimientos']+factor2['red chilies']+factor2['green chiles']

In [128]:
chili_columns_list = ['chiles','chili mix','chili powder','chili with beans','chilli powder','fresh red chili','green chilies','green chilis','pimento','pimentos','pimiento','pimientos','red chilies','green chiles']
len(chili_columns_list)

14

In [129]:
factor2 = factor2.drop(chili_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 212)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  baking potatoes  beans  beef  bell pepper  bell peppers  \
0     0.0              0.0    1.0   0.0          0.0           0.0   
1     0.0              0.0    0.0   0.0          0.0           0.0   
2     0.0              0.0    0.0   0.0          0.0           0.0   
3     1.0              0.0    0.0   0.0          0.0           0.0   
4     0.0              0.0    0.0   0.0          0.0           0.0   

   biscuit baking mix  biscuit mix  black olives  black-eyed peas  bread  \
0                 0.0          0.0           0.0              0.0    0.0   
1                 0.0          0.0           0.0              0.0    0.0   
2                 0.0          0.0           0.0              0.0    0.0   
3                 0.0          0.0           0.0              0.0    0.0   
4                 0.0          0.0           0.0              0.0    0.0   

   breyers golden vanilla ice cream  brown  brown potatoes  brown rice  \
0                               0.0    0.0             0.0         0.0   
1                               0.0    0.0             0.0         0.0   
2                               0.0    0.0             0.0         0.0   
3                               0.0    0.0             0.0         0.0   
4                               0.0    0.0             0.0         0.0   

   brown sugar  butter  castor sugar  cereal  cheerios  cheese  chick peas  \
0          1.0     0.0           0.0     0.0       0.0     0.0         0.0   
1          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
2          0.0     2.0           0.0     0.0       0.0     0.0         0.0   
3          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
4          0.0     1.0           0.0     0.0       0.0     1.0         0.0   

   chicken  chocolate  chocolate ice cream  coconut  coconut cream  \
0      0.0        0.0                  0.0      0.0            0.0   
1      0.0        0.0                  0.0      0.0            0.0   
2      1.0        0.0                  0.0      0.0            0.0   
3      0.0        0.0                  0.0      0.0            0.0   
4      0.0        0.0                  0.0      0.0            0.0   

   coconut cream filling  coconut extract  coconut flakes  \
0                    0.0              0.0             0.0   
1                    0.0              0.0             0.0   
2                    0.0              0.0             0.0   
3                    0.0              0.0             0.0   
4                    0.0              0.0             0.0   

   confectioners sugar  cookie crumbs  cookie dough  corn  corn bread  \
0                  0.0            0.0           0.0   0.0         0.0   
1                  0.0            0.0           0.0   0.0         0.0   
2                  0.0            0.0           0.0   0.0         0.0   
3                  0.0            0.0           0.0   0.0         0.0   
4                  0.0            0.0           0.0   0.0         0.0   

   corn chips  corn flakes  corn meal  corn muffin  corn tortillas  \
0         0.0          0.0        0.0          0.0             0.0   
1         0.0          0.0        0.0          0.0             0.0   
2         0.0          0.0        0.0          0.0             0.0   
3         0.0          0.0        0.0          0.0             0.0   
4         0.0          0.0        0.0          0.0             0.0   

   cornflakes  cracker crumbs  crackers  cracklins  cream of celery  \
0         0.0             0.0       0.0        0.0      

### Bell Pepper group

In [130]:
factor2['bell_pepper'] = factor2['bell pepper']+factor2['bell peppers']+factor2['green bell pepper']+factor2['paprika']+factor2['pickles']+factor2['pickling salt']+factor2['pickling spice']+factor2['red pepper']+factor2['red peppers']+factor2['sweet pepper']+factor2['sweet pickle']+factor2['sweet pickle juice']+factor2['sweet pickle relish']+factor2['sweet red pepper']

In [131]:
bell_columns_list = ['bell pepper','bell peppers','green bell pepper','paprika','pickles','pickling salt','pickling spice','red pepper','red peppers','sweet pepper','sweet pickle','sweet pickle juice','sweet pickle relish','sweet red pepper']
len(bell_columns_list)

14

In [132]:
factor2 = factor2.drop(bell_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 199)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  baking potatoes  beans  beef  biscuit baking mix  biscuit mix  \
0     0.0              0.0    1.0   0.0                 0.0          0.0   
1     0.0              0.0    0.0   0.0                 0.0          0.0   
2     0.0              0.0    0.0   0.0                 0.0          0.0   
3     1.0              0.0    0.0   0.0                 0.0          0.0   
4     0.0              0.0    0.0   0.0                 0.0          0.0   

   black olives  black-eyed peas  bread  breyers golden vanilla ice cream  \
0           0.0              0.0    0.0                               0.0   
1           0.0              0.0    0.0                               0.0   
2           0.0              0.0    0.0                               0.0   
3           0.0              0.0    0.0                               0.0   
4           0.0              0.0    0.0                               0.0   

   brown  brown potatoes  brown rice  brown sugar  butter  castor sugar  \
0    0.0             0.0         0.0          1.0     0.0           0.0   
1    0.0             0.0         0.0          0.0     0.0           0.0   
2    0.0             0.0         0.0          0.0     2.0           0.0   
3    0.0             0.0         0.0          0.0     0.0           0.0   
4    0.0             0.0         0.0          0.0     1.0           0.0   

   cereal  cheerios  cheese  chick peas  chicken  chocolate  \
0     0.0       0.0     0.0         0.0      0.0        0.0   
1     0.0       0.0     1.0         0.0      0.0        0.0   
2     0.0       0.0     0.0         0.0      1.0        0.0   
3     0.0       0.0     1.0         0.0      0.0        0.0   
4     0.0       0.0     1.0         0.0      0.0        0.0   

   chocolate ice cream  coconut  coconut cream  coconut cream filling  \
0                  0.0      0.0            0.0                    0.0   
1                  0.0      0.0            0.0                    0.0   
2                  0.0      0.0            0.0                    0.0   
3                  0.0      0.0            0.0                    0.0   
4                  0.0      0.0            0.0                    0.0   

   coconut extract  coconut flakes  confectioners sugar  cookie crumbs  \
0              0.0             0.0                  0.0            0.0   
1              0.0             0.0                  0.0            0.0   
2              0.0             0.0                  0.0            0.0   
3              0.0             0.0                  0.0            0.0   
4              0.0             0.0                  0.0            0.0   

   cookie dough  corn  corn bread  corn chips  corn flakes  corn meal  \
0           0.0   0.0         0.0         0.0          0.0        0.0   
1           0.0   0.0         0.0         0.0          0.0        0.0   
2           0.0   0.0         0.0         0.0          0.0        0.0   
3           0.0   0.0         0.0         0.0          0.0        0.0   
4           0.0   0.0         0.0         0.0          0.0        0.0   

   corn muffin  corn tortillas  cornflakes  cracker crumbs  crackers  \
0          0.0             0.0         0.0             0.0       0.0   
1          0.0             0.0         0.0             1.0       0.0   
2          0.0             0.0         0.0             0.0       0.0   
3          0.0             0.0         0.0             0.0       0.0   
4          0.0             0.0         0.0             0.0       0.0   

   cracklins  cream of celery  cream of chicken  cream of coc

### Pork group

In [133]:
factor2['pork'] = factor2['cracklins']+factor2['fresh ground pork']+factor2['fresh pork']+factor2['ground lean pork']+factor2['ground pork']+factor2['pork']+factor2['pork chops']+factor2['pork loin']+factor2['pork loin chops']+factor2['pork roast']+factor2['pork sausage']+factor2['pork shoulder']+factor2['pork tenderloin']+factor2['salt pork']

In [134]:
pork_columns_list = ['cracklins','fresh ground pork','fresh pork','ground lean pork','ground pork','pork chops','pork loin','pork loin chops','pork roast','pork sausage','pork shoulder','pork tenderloin','salt pork']
len(pork_columns_list)

13

In [135]:
factor2 = factor2.drop(pork_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 186)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  baking potatoes  beans  beef  biscuit baking mix  biscuit mix  \
0     0.0              0.0    1.0   0.0                 0.0          0.0   
1     0.0              0.0    0.0   0.0                 0.0          0.0   
2     0.0              0.0    0.0   0.0                 0.0          0.0   
3     1.0              0.0    0.0   0.0                 0.0          0.0   
4     0.0              0.0    0.0   0.0                 0.0          0.0   

   black olives  black-eyed peas  bread  breyers golden vanilla ice cream  \
0           0.0              0.0    0.0                               0.0   
1           0.0              0.0    0.0                               0.0   
2           0.0              0.0    0.0                               0.0   
3           0.0              0.0    0.0                               0.0   
4           0.0              0.0    0.0                               0.0   

   brown  brown potatoes  brown rice  brown sugar  butter  castor sugar  \
0    0.0             0.0         0.0          1.0     0.0           0.0   
1    0.0             0.0         0.0          0.0     0.0           0.0   
2    0.0             0.0         0.0          0.0     2.0           0.0   
3    0.0             0.0         0.0          0.0     0.0           0.0   
4    0.0             0.0         0.0          0.0     1.0           0.0   

   cereal  cheerios  cheese  chick peas  chicken  chocolate  \
0     0.0       0.0     0.0         0.0      0.0        0.0   
1     0.0       0.0     1.0         0.0      0.0        0.0   
2     0.0       0.0     0.0         0.0      1.0        0.0   
3     0.0       0.0     1.0         0.0      0.0        0.0   
4     0.0       0.0     1.0         0.0      0.0        0.0   

   chocolate ice cream  coconut  coconut cream  coconut cream filling  \
0                  0.0      0.0            0.0                    0.0   
1                  0.0      0.0            0.0                    0.0   
2                  0.0      0.0            0.0                    0.0   
3                  0.0      0.0            0.0                    0.0   
4                  0.0      0.0            0.0                    0.0   

   coconut extract  coconut flakes  confectioners sugar  cookie crumbs  \
0              0.0             0.0                  0.0            0.0   
1              0.0             0.0                  0.0            0.0   
2              0.0             0.0                  0.0            0.0   
3              0.0             0.0                  0.0            0.0   
4              0.0             0.0                  0.0            0.0   

   cookie dough  corn  corn bread  corn chips  corn flakes  corn meal  \
0           0.0   0.0         0.0         0.0          0.0        0.0   
1           0.0   0.0         0.0         0.0          0.0        0.0   
2           0.0   0.0         0.0         0.0          0.0        0.0   
3           0.0   0.0         0.0         0.0          0.0        0.0   
4           0.0   0.0         0.0         0.0          0.0        0.0   

   corn muffin  corn tortillas  cornflakes  cracker crumbs  crackers  \
0          0.0             0.0         0.0             0.0       0.0   
1          0.0             0.0         0.0             1.0       0.0   
2          0.0             0.0         0.0             0.0       0.0   
3          0.0             0.0         0.0             0.0       0.0   
4          0.0             0.0         0.0             0.0       0.0   

   cream of celery  cream of chicken  cream of coconut  cream

### Pie Cookies Group

In [136]:
factor2['pie_cookies'] = factor2['biscuit baking mix']+factor2['biscuit mix']+factor2['cookie crumbs']+factor2['cookie dough']+factor2['mint cookies']+factor2['oreo cookies']+factor2['oreos']+factor2['pie crust']+factor2['pie shell']+factor2['pie shells']+factor2['regular biscuits']+factor2['unbaked pie crusts']+factor2['unbaked pie shell']

In [137]:
pie_columns_list = ['biscuit baking mix','biscuit mix','cookie crumbs','cookie dough','mint cookies','oreo cookies','oreos','pie crust','pie shell','pie shells','regular biscuits','unbaked pie crusts','unbaked pie shell']
len(pie_columns_list)

13

In [138]:
factor2 = factor2.drop(pie_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 174)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  baking potatoes  beans  beef  black olives  black-eyed peas  bread  \
0     0.0              0.0    1.0   0.0           0.0              0.0    0.0   
1     0.0              0.0    0.0   0.0           0.0              0.0    0.0   
2     0.0              0.0    0.0   0.0           0.0              0.0    0.0   
3     1.0              0.0    0.0   0.0           0.0              0.0    0.0   
4     0.0              0.0    0.0   0.0           0.0              0.0    0.0   

   breyers golden vanilla ice cream  brown  brown potatoes  brown rice  \
0                               0.0    0.0             0.0         0.0   
1                               0.0    0.0             0.0         0.0   
2                               0.0    0.0             0.0         0.0   
3                               0.0    0.0             0.0         0.0   
4                               0.0    0.0             0.0         0.0   

   brown sugar  butter  castor sugar  cereal  cheerios  cheese  chick peas  \
0          1.0     0.0           0.0     0.0       0.0     0.0         0.0   
1          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
2          0.0     2.0           0.0     0.0       0.0     0.0         0.0   
3          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
4          0.0     1.0           0.0     0.0       0.0     1.0         0.0   

   chicken  chocolate  chocolate ice cream  coconut  coconut cream  \
0      0.0        0.0                  0.0      0.0            0.0   
1      0.0        0.0                  0.0      0.0            0.0   
2      1.0        0.0                  0.0      0.0            0.0   
3      0.0        0.0                  0.0      0.0            0.0   
4      0.0        0.0                  0.0      0.0            0.0   

   coconut cream filling  coconut extract  coconut flakes  \
0                    0.0              0.0             0.0   
1                    0.0              0.0             0.0   
2                    0.0              0.0             0.0   
3                    0.0              0.0             0.0   
4                    0.0              0.0             0.0   

   confectioners sugar  corn  corn bread  corn chips  corn flakes  corn meal  \
0                  0.0   0.0         0.0         0.0          0.0        0.0   
1                  0.0   0.0         0.0         0.0          0.0        0.0   
2                  0.0   0.0         0.0         0.0          0.0        0.0   
3                  0.0   0.0         0.0         0.0          0.0        0.0   
4                  0.0   0.0         0.0         0.0          0.0        0.0   

   corn muffin  corn tortillas  cornflakes  cracker crumbs  crackers  \
0          0.0             0.0         0.0             0.0       0.0   
1          0.0             0.0         0.0             1.0       0.0   
2          0.0             0.0         0.0             0.0       0.0   
3          0.0             0.0         0.0             0.0       0.0   
4          0.0             0.0         0.0             0.0       0.0   

   cream of celery  cream of chicken  cream of coconut  cream of tartar  \
0              0.0               0.0               0.0              0.0   
1              0.0               0.0               0.0              0.0   
2              0.0               1.0               0.0              0.0   
3              0.0               0.0               0.0              0.0   
4              0.0               0.0               0.0              0.0   

   cream sher

### Crackers Group

In [139]:
factor2['crackers'] = factor2['corn flakes']+factor2['cornflakes']+factor2['cracker crumbs']+factor2['crackers']+factor2['graham cracker crumbs']+factor2['graham cracker crust']+factor2['graham cracker crusts']+factor2['graham cracker pie crust']+factor2['graham cracker shells']+factor2['graham crackers']+factor2['oyster crackers']+factor2['saltine crackers']+factor2['waverly crackers']

In [140]:
crackers_columns_list = ['corn flakes','cornflakes','cracker crumbs','graham cracker crumbs','graham cracker crust','graham cracker crusts','graham cracker pie crust','graham cracker shells','graham crackers','oyster crackers','saltine crackers','waverly crackers']
len(crackers_columns_list)

12

In [141]:
factor2 = factor2.drop(crackers_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 162)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  baking potatoes  beans  beef  black olives  black-eyed peas  bread  \
0     0.0              0.0    1.0   0.0           0.0              0.0    0.0   
1     0.0              0.0    0.0   0.0           0.0              0.0    0.0   
2     0.0              0.0    0.0   0.0           0.0              0.0    0.0   
3     1.0              0.0    0.0   0.0           0.0              0.0    0.0   
4     0.0              0.0    0.0   0.0           0.0              0.0    0.0   

   breyers golden vanilla ice cream  brown  brown potatoes  brown rice  \
0                               0.0    0.0             0.0         0.0   
1                               0.0    0.0             0.0         0.0   
2                               0.0    0.0             0.0         0.0   
3                               0.0    0.0             0.0         0.0   
4                               0.0    0.0             0.0         0.0   

   brown sugar  butter  castor sugar  cereal  cheerios  cheese  chick peas  \
0          1.0     0.0           0.0     0.0       0.0     0.0         0.0   
1          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
2          0.0     2.0           0.0     0.0       0.0     0.0         0.0   
3          0.0     0.0           0.0     0.0       0.0     1.0         0.0   
4          0.0     1.0           0.0     0.0       0.0     1.0         0.0   

   chicken  chocolate  chocolate ice cream  coconut  coconut cream  \
0      0.0        0.0                  0.0      0.0            0.0   
1      0.0        0.0                  0.0      0.0            0.0   
2      1.0        0.0                  0.0      0.0            0.0   
3      0.0        0.0                  0.0      0.0            0.0   
4      0.0        0.0                  0.0      0.0            0.0   

   coconut cream filling  coconut extract  coconut flakes  \
0                    0.0              0.0             0.0   
1                    0.0              0.0             0.0   
2                    0.0              0.0             0.0   
3                    0.0              0.0             0.0   
4                    0.0              0.0             0.0   

   confectioners sugar  corn  corn bread  corn chips  corn meal  corn muffin  \
0                  0.0   0.0         0.0         0.0        0.0          0.0   
1                  0.0   0.0         0.0         0.0        0.0          0.0   
2                  0.0   0.0         0.0         0.0        0.0          0.0   
3                  0.0   0.0         0.0         0.0        0.0          0.0   
4                  0.0   0.0         0.0         0.0        0.0          0.0   

   corn tortillas  crackers  cream of celery  cream of chicken  \
0             0.0       0.0              0.0               0.0   
1             0.0       1.0              0.0               0.0   
2             0.0       0.0              0.0               1.0   
3             0.0       0.0              0.0               0.0   
4             0.0       0.0              0.0               0.0   

   cream of coconut  cream of tartar  cream sherry  cream-style  \
0               0.0              0.0           0.0          0.0   
1               0.0              0.0           0.0          0.0   
2               0.0              0.0           0.0          0.0   
3               0.0              0.0           0.0          0.0   
4               0.0              0.0           0.0          0.0   

   cream-style corn  cream-style cottage cheese  crisp rice cereal  doritos  \
0               0.

### Potato Group

In [142]:
factor2['potato'] = factor2['baking potatoes']+factor2['brown potatoes']+factor2['frozen hash browns']+factor2['frozen hashbrowns']+factor2['hash browns']+factor2['hot mashed potatoes']+factor2['mashed potatoes']+factor2['potato']+factor2['potato slices']+factor2['potatoes']+factor2['red new potatoes']+factor2['red potatoes']+factor2['sweet potatoes']

In [143]:
potato_columns_list = ['baking potatoes','brown potatoes','frozen hash browns','frozen hashbrowns','hash browns','hot mashed potatoes','mashed potatoes','potato slices','potatoes','red new potatoes','red potatoes','sweet potatoes']
len(potato_columns_list)

12

In [144]:
factor2 = factor2.drop(potato_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 150)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  beans  beef  black olives  black-eyed peas  bread  \
0     0.0    1.0   0.0           0.0              0.0    0.0   
1     0.0    0.0   0.0           0.0              0.0    0.0   
2     0.0    0.0   0.0           0.0              0.0    0.0   
3     1.0    0.0   0.0           0.0              0.0    0.0   
4     0.0    0.0   0.0           0.0              0.0    0.0   

   breyers golden vanilla ice cream  brown  brown rice  brown sugar  butter  \
0                               0.0    0.0         0.0          1.0     0.0   
1                               0.0    0.0         0.0          0.0     0.0   
2                               0.0    0.0         0.0          0.0     2.0   
3                               0.0    0.0         0.0          0.0     0.0   
4                               0.0    0.0         0.0          0.0     1.0   

   castor sugar  cereal  cheerios  cheese  chick peas  chicken  chocolate  \
0           0.0     0.0       0.0     0.0         0.0      0.0        0.0   
1           0.0     0.0       0.0     1.0         0.0      0.0        0.0   
2           0.0     0.0       0.0     0.0         0.0      1.0        0.0   
3           0.0     0.0       0.0     1.0         0.0      0.0        0.0   
4           0.0     0.0       0.0     1.0         0.0      0.0        0.0   

   chocolate ice cream  coconut  coconut cream  coconut cream filling  \
0                  0.0      0.0            0.0                    0.0   
1                  0.0      0.0            0.0                    0.0   
2                  0.0      0.0            0.0                    0.0   
3                  0.0      0.0            0.0                    0.0   
4                  0.0      0.0            0.0                    0.0   

   coconut extract  coconut flakes  confectioners sugar  corn  corn bread  \
0              0.0             0.0                  0.0   0.0         0.0   
1              0.0             0.0                  0.0   0.0         0.0   
2              0.0             0.0                  0.0   0.0         0.0   
3              0.0             0.0                  0.0   0.0         0.0   
4              0.0             0.0                  0.0   0.0         0.0   

   corn chips  corn meal  corn muffin  corn tortillas  crackers  \
0         0.0        0.0          0.0             0.0       0.0   
1         0.0        0.0          0.0             0.0       1.0   
2         0.0        0.0          0.0             0.0       0.0   
3         0.0        0.0          0.0             0.0       0.0   
4         0.0        0.0          0.0             0.0       0.0   

   cream of celery  cream of chicken  cream of coconut  cream of tartar  \
0              0.0               0.0               0.0              0.0   
1              0.0               0.0               0.0              0.0   
2              0.0               1.0               0.0              0.0   
3              0.0               0.0               0.0              0.0   
4              0.0               0.0               0.0              0.0   

   cream sherry  cream-style  cream-style corn  cream-style cottage cheese  \
0           0.0          0.0               0.0                         0.0   
1           0.0          0.0               0.0                         0.0   
2           0.0          0.0               0.0                         0.0   
3           0.0          0.0               0.0                         0.0   
4           0.0          0.0               0.0                         0.0   

   crisp rice cerea

### Chips Group

In [145]:
factor2['chips'] = factor2['corn tortillas']+factor2['doritos']+factor2['doritos chips']+factor2['nacho chips']+factor2['nachos']+factor2['potato chips']+factor2['sack favorite tortilla']+factor2['sack tortilla chips']+factor2['taco']+factor2['taco seasoning']+factor2['taco seasoning mix']+factor2['tortilla chips']+factor2['tortillas']

In [146]:
chips_columns_list = ['corn tortillas','doritos','doritos chips','nacho chips','nachos','potato chips','sack favorite tortilla','sack tortilla chips','taco','taco seasoning','taco seasoning mix','tortilla chips','tortillas']
len(chips_columns_list)

13

In [147]:
factor2 = factor2.drop(chips_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 138)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  beans  beef  black olives  black-eyed peas  bread  \
0     0.0    1.0   0.0           0.0              0.0    0.0   
1     0.0    0.0   0.0           0.0              0.0    0.0   
2     0.0    0.0   0.0           0.0              0.0    0.0   
3     1.0    0.0   0.0           0.0              0.0    0.0   
4     0.0    0.0   0.0           0.0              0.0    0.0   

   breyers golden vanilla ice cream  brown  brown rice  brown sugar  butter  \
0                               0.0    0.0         0.0          1.0     0.0   
1                               0.0    0.0         0.0          0.0     0.0   
2                               0.0    0.0         0.0          0.0     2.0   
3                               0.0    0.0         0.0          0.0     0.0   
4                               0.0    0.0         0.0          0.0     1.0   

   castor sugar  cereal  cheerios  cheese  chick peas  chicken  chocolate  \
0           0.0     0.0       0.0     0.0         0.0      0.0        0.0   
1           0.0     0.0       0.0     1.0         0.0      0.0        0.0   
2           0.0     0.0       0.0     0.0         0.0      1.0        0.0   
3           0.0     0.0       0.0     1.0         0.0      0.0        0.0   
4           0.0     0.0       0.0     1.0         0.0      0.0        0.0   

   chocolate ice cream  coconut  coconut cream  coconut cream filling  \
0                  0.0      0.0            0.0                    0.0   
1                  0.0      0.0            0.0                    0.0   
2                  0.0      0.0            0.0                    0.0   
3                  0.0      0.0            0.0                    0.0   
4                  0.0      0.0            0.0                    0.0   

   coconut extract  coconut flakes  confectioners sugar  corn  corn bread  \
0              0.0             0.0                  0.0   0.0         0.0   
1              0.0             0.0                  0.0   0.0         0.0   
2              0.0             0.0                  0.0   0.0         0.0   
3              0.0             0.0                  0.0   0.0         0.0   
4              0.0             0.0                  0.0   0.0         0.0   

   corn chips  corn meal  corn muffin  crackers  cream of celery  \
0         0.0        0.0          0.0       0.0              0.0   
1         0.0        0.0          0.0       1.0              0.0   
2         0.0        0.0          0.0       0.0              0.0   
3         0.0        0.0          0.0       0.0              0.0   
4         0.0        0.0          0.0       0.0              0.0   

   cream of chicken  cream of coconut  cream of tartar  cream sherry  \
0               0.0               0.0              0.0           0.0   
1               0.0               0.0              0.0           0.0   
2               1.0               0.0              0.0           0.0   
3               0.0               0.0              0.0           0.0   
4               0.0               0.0              0.0           0.0   

   cream-style  cream-style corn  cream-style cottage cheese  \
0          0.0               0.0                         0.0   
1          0.0               0.0                         0.0   
2          0.0               0.0                         0.0   
3          0.0               0.0                         0.0   
4          0.0               0.0                         0.0   

   crisp rice cereal  dream whip  dream whip topping mix  egg  egg noodles  \
0                0.0         0.0     

### Whipped Cream Group

In [148]:
factor2['whipped'] = factor2['breyers golden vanilla ice cream']+factor2['chocolate ice cream']+factor2['dream whip']+factor2['dream whip topping mix']+factor2['frozen whipped topping']+factor2['green sherbet']+factor2['nondairy creamer']+factor2['nondairy whipped topping']+factor2['vanilla ice cream']+factor2['whipped cream']+factor2['whipped topping']+factor2['whipping cream']

In [149]:
whipped_columns_list = ['breyers golden vanilla ice cream','chocolate ice cream','dream whip','dream whip topping mix','frozen whipped topping','green sherbet','nondairy creamer','nondairy whipped topping','vanilla ice cream','whipped cream','whipped topping','whipping cream']
len(whipped_columns_list)

12

In [150]:
factor2 = factor2.drop(whipped_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 127)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  beans  beef  black olives  black-eyed peas  bread  brown  \
0     0.0    1.0   0.0           0.0              0.0    0.0    0.0   
1     0.0    0.0   0.0           0.0              0.0    0.0    0.0   
2     0.0    0.0   0.0           0.0              0.0    0.0    0.0   
3     1.0    0.0   0.0           0.0              0.0    0.0    0.0   
4     0.0    0.0   0.0           0.0              0.0    0.0    0.0   

   brown rice  brown sugar  butter  castor sugar  cereal  cheerios  cheese  \
0         0.0          1.0     0.0           0.0     0.0       0.0     0.0   
1         0.0          0.0     0.0           0.0     0.0       0.0     1.0   
2         0.0          0.0     2.0           0.0     0.0       0.0     0.0   
3         0.0          0.0     0.0           0.0     0.0       0.0     1.0   
4         0.0          0.0     1.0           0.0     0.0       0.0     1.0   

   chick peas  chicken  chocolate  coconut  coconut cream  \
0         0.0      0.0        0.0      0.0            0.0   
1         0.0      0.0        0.0      0.0            0.0   
2         0.0      1.0        0.0      0.0            0.0   
3         0.0      0.0        0.0      0.0            0.0   
4         0.0      0.0        0.0      0.0            0.0   

   coconut cream filling  coconut extract  coconut flakes  \
0                    0.0              0.0             0.0   
1                    0.0              0.0             0.0   
2                    0.0              0.0             0.0   
3                    0.0              0.0             0.0   
4                    0.0              0.0             0.0   

   confectioners sugar  corn  corn bread  corn chips  corn meal  corn muffin  \
0                  0.0   0.0         0.0         0.0        0.0          0.0   
1                  0.0   0.0         0.0         0.0        0.0          0.0   
2                  0.0   0.0         0.0         0.0        0.0          0.0   
3                  0.0   0.0         0.0         0.0        0.0          0.0   
4                  0.0   0.0         0.0         0.0        0.0          0.0   

   crackers  cream of celery  cream of chicken  cream of coconut  \
0       0.0              0.0               0.0               0.0   
1       1.0              0.0               0.0               0.0   
2       0.0              0.0               1.0               0.0   
3       0.0              0.0               0.0               0.0   
4       0.0              0.0               0.0               0.0   

   cream of tartar  cream sherry  cream-style  cream-style corn  \
0              0.0           0.0          0.0               0.0   
1              0.0           0.0          0.0               0.0   
2              0.0           0.0          0.0               0.0   
3              0.0           0.0          0.0               0.0   
4              0.0           0.0          0.0               0.0   

   cream-style cottage cheese  crisp rice cereal  egg  egg noodles  egg roll  \
0                         0.0                0.0  0.0          0.0       0.0   
1                         0.0                0.0  0.0          0.0       0.0   
2                         0.0                0.0  0.0          0.0       0.0   
3                         0.0                0.0  0.0          0.0       0.0   
4                         0.0                0.0  0.0          0.0       0.0   

   egg substitute  egg white  egg whites  egg yolk  egg yolks  eggs  \
0             0.0        0.0         0.0       0.0        0.0   0.0   
1             0.0    

### Cream Cuisines Group

In [151]:
factor2['cream'] = factor2['cream of celery']+factor2['cream of chicken']+factor2['cream of tartar']+factor2['cream sherry']+factor2['cream-style']+factor2['cream-style corn']+factor2['cream-style cottage cheese']+factor2['nonfat plain yogurt']+factor2['nonfat yogurt']+factor2['plain yogurt']+factor2['vanilla low-fat yogurt']+factor2['yogurt']

In [152]:
cream_columns_list = ['cream of celery','cream of chicken','cream of tartar','cream sherry','cream-style','cream-style corn','cream-style cottage cheese','nonfat plain yogurt','nonfat yogurt','plain yogurt','vanilla low-fat yogurt','yogurt']
len(cream_columns_list)

12

In [153]:
factor2 = factor2.drop(cream_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 116)


item  angel  angel food cake  \
0  [pinto beans, cooking oil, catsup, worcestersh...    0.0              0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...    0.0              0.0   
2  [chicken, cream of chicken, margarine, flour, ...    0.0              0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...    0.0              0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...    0.0              0.0   

   apples  beans  beef  black olives  black-eyed peas  bread  brown  \
0     0.0    1.0   0.0           0.0              0.0    0.0    0.0   
1     0.0    0.0   0.0           0.0              0.0    0.0    0.0   
2     0.0    0.0   0.0           0.0              0.0    0.0    0.0   
3     1.0    0.0   0.0           0.0              0.0    0.0    0.0   
4     0.0    0.0   0.0           0.0              0.0    0.0    0.0   

   brown rice  brown sugar  butter  castor sugar  cereal  cheerios  cheese  \
0         0.0          1.0     0.0           0.0     0.0       0.0     0.0   
1         0.0          0.0     0.0           0.0     0.0       0.0     1.0   
2         0.0          0.0     2.0           0.0     0.0       0.0     0.0   
3         0.0          0.0     0.0           0.0     0.0       0.0     1.0   
4         0.0          0.0     1.0           0.0     0.0       0.0     1.0   

   chick peas  chicken  chocolate  coconut  coconut cream  \
0         0.0      0.0        0.0      0.0            0.0   
1         0.0      0.0        0.0      0.0            0.0   
2         0.0      1.0        0.0      0.0            0.0   
3         0.0      0.0        0.0      0.0            0.0   
4         0.0      0.0        0.0      0.0            0.0   

   coconut cream filling  coconut extract  coconut flakes  \
0                    0.0              0.0             0.0   
1                    0.0              0.0             0.0   
2                    0.0              0.0             0.0   
3                    0.0              0.0             0.0   
4                    0.0              0.0             0.0   

   confectioners sugar  corn  corn bread  corn chips  corn meal  corn muffin  \
0                  0.0   0.0         0.0         0.0        0.0          0.0   
1                  0.0   0.0         0.0         0.0        0.0          0.0   
2                  0.0   0.0         0.0         0.0        0.0          0.0   
3                  0.0   0.0         0.0         0.0        0.0          0.0   
4                  0.0   0.0         0.0         0.0        0.0          0.0   

   crackers  cream of coconut  crisp rice cereal  egg  egg noodles  egg roll  \
0       0.0               0.0                0.0  0.0          0.0       0.0   
1       1.0               0.0                0.0  0.0          0.0       0.0   
2       0.0               0.0                0.0  0.0          0.0       0.0   
3       0.0               0.0                0.0  0.0          0.0       0.0   
4       0.0               0.0                0.0  0.0          0.0       0.0   

   egg substitute  egg white  egg whites  egg yolk  egg yolks  eggs  \
0             0.0        0.0         0.0       0.0        0.0   0.0   
1             0.0        0.0         0.0       0.0        0.0   1.0   
2             0.0        0.0         0.0       0.0        0.0   0.0   
3             0.0        0.0         0.0       0.0        0.0   0.0   
4             0.0        0.0         0.0       0.0        0.0   1.0   

   english peas  flaked coconut  flour  fresh corn  freshly cooked rice  \
0           0.0             0.0    1.0         0.0                  0.0   
1           0.0             0.0    0.0         0.0                  0.0   
2           0.0             0.0    1.0         0.0                  0.0   
3           0.0             0.0    0.0         0.0                  0.0   
4           0.0             0.0    0.0         0.0                  0.0   

   frozen coconut  frozen corn  frozen peas  fruit  garbanzos  garden peas  \
0             0.0  

### Coconut group

In [154]:
factor2['coconut'] = factor2['angel']+factor2['angel food cake']+factor2['coconut']+factor2['coconut cream']+factor2['coconut cream filling']+factor2['coconut extract']+factor2['coconut flakes']+factor2['cream of coconut']+factor2['flaked coconut']+factor2['frozen coconut']+factor2['grated coconut']+factor2['shredded coconut']

In [155]:
coconut_columns_list = ['angel','angel food cake','coconut cream','coconut cream filling','coconut extract','coconut flakes','cream of coconut','flaked coconut','frozen coconut','grated coconut','shredded coconut']
len(coconut_columns_list)

11

In [156]:
factor2 = factor2.drop(coconut_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 105)


item  apples  beans  beef  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0    1.0   0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0    0.0   0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0    0.0   0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     1.0    0.0   0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0    0.0   0.0   

   black olives  black-eyed peas  bread  brown  brown rice  brown sugar  \
0           0.0              0.0    0.0    0.0         0.0          1.0   
1           0.0              0.0    0.0    0.0         0.0          0.0   
2           0.0              0.0    0.0    0.0         0.0          0.0   
3           0.0              0.0    0.0    0.0         0.0          0.0   
4           0.0              0.0    0.0    0.0         0.0          0.0   

   butter  castor sugar  cereal  cheerios  cheese  chick peas  chicken  \
0     0.0           0.0     0.0       0.0     0.0         0.0      0.0   
1     0.0           0.0     0.0       0.0     1.0         0.0      0.0   
2     2.0           0.0     0.0       0.0     0.0         0.0      1.0   
3     0.0           0.0     0.0       0.0     1.0         0.0      0.0   
4     1.0           0.0     0.0       0.0     1.0         0.0      0.0   

   chocolate  coconut  confectioners sugar  corn  corn bread  corn chips  \
0        0.0      0.0                  0.0   0.0         0.0         0.0   
1        0.0      0.0                  0.0   0.0         0.0         0.0   
2        0.0      0.0                  0.0   0.0         0.0         0.0   
3        0.0      0.0                  0.0   0.0         0.0         0.0   
4        0.0      0.0                  0.0   0.0         0.0         0.0   

   corn meal  corn muffin  crackers  crisp rice cereal  egg  egg noodles  \
0        0.0          0.0       0.0                0.0  0.0          0.0   
1        0.0          0.0       1.0                0.0  0.0          0.0   
2        0.0          0.0       0.0                0.0  0.0          0.0   
3        0.0          0.0       0.0                0.0  0.0          0.0   
4        0.0          0.0       0.0                0.0  0.0          0.0   

   egg roll  egg substitute  egg white  egg whites  egg yolk  egg yolks  eggs  \
0       0.0             0.0        0.0         0.0       0.0        0.0   0.0   
1       0.0             0.0        0.0         0.0       0.0        0.0   1.0   
2       0.0             0.0        0.0         0.0       0.0        0.0   0.0   
3       0.0             0.0        0.0         0.0       0.0        0.0   0.0   
4       0.0             0.0        0.0         0.0       0.0        0.0   1.0   

   english peas  flour  fresh corn  freshly cooked rice  frozen corn  \
0           0.0    1.0         0.0                  0.0          0.0   
1           0.0    0.0         0.0                  0.0          0.0   
2           0.0    1.0         0.0                  0.0          0.0   
3           0.0    0.0         0.0                  0.0          0.0   
4           0.0    0.0         0.0                  0.0          0.0   

   frozen peas  fruit  garbanzos  garden peas  granola cereal  \
0          0.0    0.0        0.0          0.0             0.0   
1          0.0    0.0        0.0          0.0             0.0   
2          0.0    0.0        0.0          0.0             0.0   
3          0.0    0.0        0.0          0.0             0.0   
4          0.0    0.0        0.0          0.0             0.0   

   granulated sugar  green olives  kellogg  kernel corn  lemon  \
0               0.0           0.0      0.0          0.0    0.0   
1               0.0           0.0      0.0          0.0    0.0   
2               0.0           0.0      0.0          0.0    0.0   
3               0.0           0.0      0.0          0.0    1.0   
4               0.0           0.0      0.0          0.0    0.0   

   light brown sugar  long grain rice  long grain white rice  milk 

### Peas Group

In [157]:
factor2['peas'] = factor2['black olives']+factor2['black-eyed peas']+factor2['chick peas']+factor2['english peas']+factor2['frozen peas']+factor2['garbanzos']+factor2['garden peas']+factor2['green olives']+factor2['olive']+factor2['olives']+factor2['peas']+factor2['ripe olives']+factor2['snow peas']

In [158]:
peas_columns_list = ['black olives','black-eyed peas','chick peas','english peas','frozen peas','garbanzos','garden peas','green olives','olive','olives','ripe olives','snow peas']
len(peas_columns_list)

12

In [159]:
factor2 = factor2.drop(peas_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 93)


item  apples  beans  beef  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0    1.0   0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0    0.0   0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0    0.0   0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     1.0    0.0   0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0    0.0   0.0   

   bread  brown  brown rice  brown sugar  butter  castor sugar  cereal  \
0    0.0    0.0         0.0          1.0     0.0           0.0     0.0   
1    0.0    0.0         0.0          0.0     0.0           0.0     0.0   
2    0.0    0.0         0.0          0.0     2.0           0.0     0.0   
3    0.0    0.0         0.0          0.0     0.0           0.0     0.0   
4    0.0    0.0         0.0          0.0     1.0           0.0     0.0   

   cheerios  cheese  chicken  chocolate  coconut  confectioners sugar  corn  \
0       0.0     0.0      0.0        0.0      0.0                  0.0   0.0   
1       0.0     1.0      0.0        0.0      0.0                  0.0   0.0   
2       0.0     0.0      1.0        0.0      0.0                  0.0   0.0   
3       0.0     1.0      0.0        0.0      0.0                  0.0   0.0   
4       0.0     1.0      0.0        0.0      0.0                  0.0   0.0   

   corn bread  corn chips  corn meal  corn muffin  crackers  \
0         0.0         0.0        0.0          0.0       0.0   
1         0.0         0.0        0.0          0.0       1.0   
2         0.0         0.0        0.0          0.0       0.0   
3         0.0         0.0        0.0          0.0       0.0   
4         0.0         0.0        0.0          0.0       0.0   

   crisp rice cereal  egg  egg noodles  egg roll  egg substitute  egg white  \
0                0.0  0.0          0.0       0.0             0.0        0.0   
1                0.0  0.0          0.0       0.0             0.0        0.0   
2                0.0  0.0          0.0       0.0             0.0        0.0   
3                0.0  0.0          0.0       0.0             0.0        0.0   
4                0.0  0.0          0.0       0.0             0.0        0.0   

   egg whites  egg yolk  egg yolks  eggs  flour  fresh corn  \
0         0.0       0.0        0.0   0.0    1.0         0.0   
1         0.0       0.0        0.0   1.0    0.0         0.0   
2         0.0       0.0        0.0   0.0    1.0         0.0   
3         0.0       0.0        0.0   0.0    0.0         0.0   
4         0.0       0.0        0.0   1.0    0.0         0.0   

   freshly cooked rice  frozen corn  fruit  granola cereal  granulated sugar  \
0                  0.0          0.0    0.0             0.0               0.0   
1                  0.0          0.0    0.0             0.0               0.0   
2                  0.0          0.0    0.0             0.0               0.0   
3                  0.0          0.0    0.0             0.0               0.0   
4                  0.0          0.0    0.0             0.0               0.0   

   kellogg  kernel corn  lemon  light brown sugar  long grain rice  \
0      0.0          0.0    0.0                0.0              0.0   
1      0.0          0.0    0.0                0.0              0.0   
2      0.0          0.0    0.0                0.0              0.0   
3      0.0          0.0    1.0                0.0              0.0   
4      0.0          0.0    0.0                0.0              0.0   

   long grain white rice  milk  niblets corn  noodles  nuts  oranges  pasta  \
0                    0.0   0.0           0.0      0.0   0.0      0.0    0.0   
1                    0.0   0.0           0.0      0.0   0.0      0.0    0.0   
2                    0.0   0.0           0.0      0.0   0.0      0.0    0.0   
3                    0.0   0.0           0.0      0.0   1.0      0.0    0.0   
4                    0.0   1.0           0.0      0.0   0.0      0.0    1.0   

   peas  peg white corn  pepper  popcorn  pork  potato 

### Sugar group

In [160]:
factor2['sugar'] = factor2['brown']+factor2['brown sugar']+factor2['castor sugar']+factor2['confectioners sugar']+factor2['granulated sugar']+factor2['light brown sugar']+factor2['powdered confectioners sugar']+factor2['powdered sugar']+factor2['sugar']+factor2['sweetener']+factor2['white sugar']+factor2['xxxx sugar']

In [161]:
sugar_columns_list = ['brown','brown sugar','castor sugar','confectioners sugar','granulated sugar','light brown sugar','powdered confectioners sugar','powdered sugar','sweetener','white sugar','xxxx sugar']
len(sugar_columns_list)

11

In [162]:
factor2 = factor2.drop(sugar_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 82)


item  apples  beans  beef  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0    1.0   0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0    0.0   0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0    0.0   0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     1.0    0.0   0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0    0.0   0.0   

   bread  brown rice  butter  cereal  cheerios  cheese  chicken  chocolate  \
0    0.0         0.0     0.0     0.0       0.0     0.0      0.0        0.0   
1    0.0         0.0     0.0     0.0       0.0     1.0      0.0        0.0   
2    0.0         0.0     2.0     0.0       0.0     0.0      1.0        0.0   
3    0.0         0.0     0.0     0.0       0.0     1.0      0.0        0.0   
4    0.0         0.0     1.0     0.0       0.0     1.0      0.0        0.0   

   coconut  corn  corn bread  corn chips  corn meal  corn muffin  crackers  \
0      0.0   0.0         0.0         0.0        0.0          0.0       0.0   
1      0.0   0.0         0.0         0.0        0.0          0.0       1.0   
2      0.0   0.0         0.0         0.0        0.0          0.0       0.0   
3      0.0   0.0         0.0         0.0        0.0          0.0       0.0   
4      0.0   0.0         0.0         0.0        0.0          0.0       0.0   

   crisp rice cereal  egg  egg noodles  egg roll  egg substitute  egg white  \
0                0.0  0.0          0.0       0.0             0.0        0.0   
1                0.0  0.0          0.0       0.0             0.0        0.0   
2                0.0  0.0          0.0       0.0             0.0        0.0   
3                0.0  0.0          0.0       0.0             0.0        0.0   
4                0.0  0.0          0.0       0.0             0.0        0.0   

   egg whites  egg yolk  egg yolks  eggs  flour  fresh corn  \
0         0.0       0.0        0.0   0.0    1.0         0.0   
1         0.0       0.0        0.0   1.0    0.0         0.0   
2         0.0       0.0        0.0   0.0    1.0         0.0   
3         0.0       0.0        0.0   0.0    0.0         0.0   
4         0.0       0.0        0.0   1.0    0.0         0.0   

   freshly cooked rice  frozen corn  fruit  granola cereal  kellogg  \
0                  0.0          0.0    0.0             0.0      0.0   
1                  0.0          0.0    0.0             0.0      0.0   
2                  0.0          0.0    0.0             0.0      0.0   
3                  0.0          0.0    0.0             0.0      0.0   
4                  0.0          0.0    0.0             0.0      0.0   

   kernel corn  lemon  long grain rice  long grain white rice  milk  \
0          0.0    0.0              0.0                    0.0   0.0   
1          0.0    0.0              0.0                    0.0   0.0   
2          0.0    0.0              0.0                    0.0   0.0   
3          0.0    1.0              0.0                    0.0   0.0   
4          0.0    0.0              0.0                    0.0   1.0   

   niblets corn  noodles  nuts  oranges  pasta  peas  peg white corn  pepper  \
0           0.0      0.0   0.0      0.0    0.0   0.0             0.0     0.0   
1           0.0      0.0   0.0      0.0    0.0   0.0             0.0     0.0   
2           0.0      0.0   0.0      0.0    0.0   0.0             0.0     0.0   
3           0.0      0.0   1.0      0.0    0.0   0.0             0.0     0.0   
4           0.0      0.0   0.0      0.0    1.0   0.0             0.0     0.0   

   popcorn  pork  potato  ramen noodles  ramen soup noodles  rice  \
0      0.0   0.0     0.0            0.0                 0.0   0.0   
1      0.0   0.0     0.0            0.0                 0.0   0.0   
2      0.0   0.0     0.0            0.0                 0.0   0.0   
3      0.0   0.0     0.0            0.0                 0.0   0.0   
4      0.0   0.0     0.0            0.0                 0.0   0.0   

   rice cereal  rice krispies  sauce  soba 

### Corn Group

In [163]:
factor2['corn'] = factor2['corn']+factor2['corn bread']+factor2['corn chips']+factor2['corn meal']+factor2['corn muffin']+factor2['fresh corn']+factor2['frozen corn']+factor2['niblets corn']+factor2['peg white corn']+factor2['white corn meal']+factor2['whole kernel corn']

In [164]:
corn_columns_list = ['corn bread','corn chips','corn meal','corn muffin','fresh corn','frozen corn','niblets corn','peg white corn','white corn meal','whole kernel corn']
len(corn_columns_list)

10

In [165]:
factor2 = factor2.drop(corn_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 72)


item  apples  beans  beef  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0    1.0   0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0    0.0   0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0    0.0   0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     1.0    0.0   0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0    0.0   0.0   

   bread  brown rice  butter  cereal  cheerios  cheese  chicken  chocolate  \
0    0.0         0.0     0.0     0.0       0.0     0.0      0.0        0.0   
1    0.0         0.0     0.0     0.0       0.0     1.0      0.0        0.0   
2    0.0         0.0     2.0     0.0       0.0     0.0      1.0        0.0   
3    0.0         0.0     0.0     0.0       0.0     1.0      0.0        0.0   
4    0.0         0.0     1.0     0.0       0.0     1.0      0.0        0.0   

   coconut  corn  crackers  crisp rice cereal  egg  egg noodles  egg roll  \
0      0.0   0.0       0.0                0.0  0.0          0.0       0.0   
1      0.0   0.0       1.0                0.0  0.0          0.0       0.0   
2      0.0   0.0       0.0                0.0  0.0          0.0       0.0   
3      0.0   0.0       0.0                0.0  0.0          0.0       0.0   
4      0.0   0.0       0.0                0.0  0.0          0.0       0.0   

   egg substitute  egg white  egg whites  egg yolk  egg yolks  eggs  flour  \
0             0.0        0.0         0.0       0.0        0.0   0.0    1.0   
1             0.0        0.0         0.0       0.0        0.0   1.0    0.0   
2             0.0        0.0         0.0       0.0        0.0   0.0    1.0   
3             0.0        0.0         0.0       0.0        0.0   0.0    0.0   
4             0.0        0.0         0.0       0.0        0.0   1.0    0.0   

   freshly cooked rice  fruit  granola cereal  kellogg  kernel corn  lemon  \
0                  0.0    0.0             0.0      0.0          0.0    0.0   
1                  0.0    0.0             0.0      0.0          0.0    0.0   
2                  0.0    0.0             0.0      0.0          0.0    0.0   
3                  0.0    0.0             0.0      0.0          0.0    1.0   
4                  0.0    0.0             0.0      0.0          0.0    0.0   

   long grain rice  long grain white rice  milk  noodles  nuts  oranges  \
0              0.0                    0.0   0.0      0.0   0.0      0.0   
1              0.0                    0.0   0.0      0.0   0.0      0.0   
2              0.0                    0.0   0.0      0.0   0.0      0.0   
3              0.0                    0.0   0.0      0.0   1.0      0.0   
4              0.0                    0.0   1.0      0.0   0.0      0.0   

   pasta  peas  pepper  popcorn  pork  potato  ramen noodles  \
0    0.0   0.0     0.0      0.0   0.0     0.0            0.0   
1    0.0   0.0     0.0      0.0   0.0     0.0            0.0   
2    0.0   0.0     0.0      0.0   0.0     0.0            0.0   
3    0.0   0.0     0.0      0.0   0.0     0.0            0.0   
4    1.0   0.0     0.0      0.0   0.0     0.0            0.0   

   ramen soup noodles  rice  rice cereal  rice krispies  sauce  soba noodles  \
0                 0.0   0.0          0.0            0.0    2.0           0.0   
1                 0.0   0.0          0.0            0.0    0.0           0.0   
2                 0.0   0.0          0.0            0.0    0.0           0.0   
3                 0.0   0.0          0.0            0.0    0.0           0.0   
4                 0.0   0.0          0.0            0.0    0.0           0.0   

   sugar  unbeaten egg whites  wild rice  yellow corn meal  yellow cornmeal  \
0    1.0                  0.0        0.0               0.0              0.0   
1    0.0                  0.0        0.0               0.0              0.0   
2    0.0                  0.0        0.0               0.0              0.0   
3    1.0                  0.0        0.0               0.0              0.0   
4  

### EGG Groups

In [166]:
factor2['eggs'] = factor2['eggs']+factor2['egg']+factor2['egg roll']+factor2['egg substitute']+factor2['egg white']+factor2['egg whites']+factor2['egg yolk']+factor2['egg yolks']+factor2['unbeaten egg whites']

In [167]:
eggs_columns_list = ['egg','egg roll','egg substitute','egg white','egg whites','egg yolk','egg yolks','unbeaten egg whites']
len(eggs_columns_list)

8

In [168]:
factor2 = factor2.drop(eggs_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 64)


item  apples  beans  beef  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0    1.0   0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0    0.0   0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0    0.0   0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     1.0    0.0   0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0    0.0   0.0   

   bread  brown rice  butter  cereal  cheerios  cheese  chicken  chocolate  \
0    0.0         0.0     0.0     0.0       0.0     0.0      0.0        0.0   
1    0.0         0.0     0.0     0.0       0.0     1.0      0.0        0.0   
2    0.0         0.0     2.0     0.0       0.0     0.0      1.0        0.0   
3    0.0         0.0     0.0     0.0       0.0     1.0      0.0        0.0   
4    0.0         0.0     1.0     0.0       0.0     1.0      0.0        0.0   

   coconut  corn  crackers  crisp rice cereal  egg noodles  eggs  flour  \
0      0.0   0.0       0.0                0.0          0.0   0.0    1.0   
1      0.0   0.0       1.0                0.0          0.0   1.0    0.0   
2      0.0   0.0       0.0                0.0          0.0   0.0    1.0   
3      0.0   0.0       0.0                0.0          0.0   0.0    0.0   
4      0.0   0.0       0.0                0.0          0.0   1.0    0.0   

   freshly cooked rice  fruit  granola cereal  kellogg  kernel corn  lemon  \
0                  0.0    0.0             0.0      0.0          0.0    0.0   
1                  0.0    0.0             0.0      0.0          0.0    0.0   
2                  0.0    0.0             0.0      0.0          0.0    0.0   
3                  0.0    0.0             0.0      0.0          0.0    1.0   
4                  0.0    0.0             0.0      0.0          0.0    0.0   

   long grain rice  long grain white rice  milk  noodles  nuts  oranges  \
0              0.0                    0.0   0.0      0.0   0.0      0.0   
1              0.0                    0.0   0.0      0.0   0.0      0.0   
2              0.0                    0.0   0.0      0.0   0.0      0.0   
3              0.0                    0.0   0.0      0.0   1.0      0.0   
4              0.0                    0.0   1.0      0.0   0.0      0.0   

   pasta  peas  pepper  popcorn  pork  potato  ramen noodles  \
0    0.0   0.0     0.0      0.0   0.0     0.0            0.0   
1    0.0   0.0     0.0      0.0   0.0     0.0            0.0   
2    0.0   0.0     0.0      0.0   0.0     0.0            0.0   
3    0.0   0.0     0.0      0.0   0.0     0.0            0.0   
4    1.0   0.0     0.0      0.0   0.0     0.0            0.0   

   ramen soup noodles  rice  rice cereal  rice krispies  sauce  soba noodles  \
0                 0.0   0.0          0.0            0.0    2.0           0.0   
1                 0.0   0.0          0.0            0.0    0.0           0.0   
2                 0.0   0.0          0.0            0.0    0.0           0.0   
3                 0.0   0.0          0.0            0.0    0.0           0.0   
4                 0.0   0.0          0.0            0.0    0.0           0.0   

   sugar  wild rice  yellow corn meal  yellow cornmeal  vegetables  \
0    1.0        0.0               0.0              0.0         0.0   
1    0.0        0.0               0.0              0.0         1.0   
2    0.0        0.0               0.0              0.0         0.0   
3    1.0        0.0               0.0              0.0         2.0   
4    0.0        0.0               0.0              0.0         0.0   

   seasonings  fruits  condiment  liquid  cake_mix  soup  oil_vinegar  fish  \
0         0.0     0.0        0.0     1.0       0.0   0.0          1.0   0.0   
1         0.0     0.0        1.0     1.0       0.0   1.0          0.0   0.0   
2         1.0     0.0        0.0     0.0       0.0   0.0          0.0   0.0   
3         0.0     1.0        0.0     0.0       0.0   0.0          0.0   0.0   
4         0.0     0.0        0.0     0.0       0.0   0.0       

### rice noodles groups

In [169]:
factor2['rice_noodle'] = factor2['brown rice']+factor2['egg noodles']+factor2['freshly cooked rice']+factor2['long grain rice']+factor2['long grain white rice']+factor2['noodles']+factor2['ramen noodles']+factor2['ramen soup noodles']+factor2['rice']+factor2['rice']+factor2['rice krispies']+factor2['soba noodles']+factor2['wild rice']

In [170]:
rice_columns_list = ['brown rice','egg noodles','freshly cooked rice','long grain rice','long grain white rice','noodles','ramen noodles','ramen soup noodles','rice','rice','rice krispies','soba noodles','wild rice']
len(rice_columns_list)

13

In [171]:
factor2 = factor2.drop(rice_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 53)


item  apples  beans  beef  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0    1.0   0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0    0.0   0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0    0.0   0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     1.0    0.0   0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0    0.0   0.0   

   bread  butter  cereal  cheerios  cheese  chicken  chocolate  coconut  corn  \
0    0.0     0.0     0.0       0.0     0.0      0.0        0.0      0.0   0.0   
1    0.0     0.0     0.0       0.0     1.0      0.0        0.0      0.0   0.0   
2    0.0     2.0     0.0       0.0     0.0      1.0        0.0      0.0   0.0   
3    0.0     0.0     0.0       0.0     1.0      0.0        0.0      0.0   0.0   
4    0.0     1.0     0.0       0.0     1.0      0.0        0.0      0.0   0.0   

   crackers  crisp rice cereal  eggs  flour  fruit  granola cereal  kellogg  \
0       0.0                0.0   0.0    1.0    0.0             0.0      0.0   
1       1.0                0.0   1.0    0.0    0.0             0.0      0.0   
2       0.0                0.0   0.0    1.0    0.0             0.0      0.0   
3       0.0                0.0   0.0    0.0    0.0             0.0      0.0   
4       0.0                0.0   1.0    0.0    0.0             0.0      0.0   

   kernel corn  lemon  milk  nuts  oranges  pasta  peas  pepper  popcorn  \
0          0.0    0.0   0.0   0.0      0.0    0.0   0.0     0.0      0.0   
1          0.0    0.0   0.0   0.0      0.0    0.0   0.0     0.0      0.0   
2          0.0    0.0   0.0   0.0      0.0    0.0   0.0     0.0      0.0   
3          0.0    1.0   0.0   1.0      0.0    0.0   0.0     0.0      0.0   
4          0.0    0.0   1.0   0.0      0.0    1.0   0.0     0.0      0.0   

   pork  potato  rice cereal  sauce  sugar  yellow corn meal  yellow cornmeal  \
0   0.0     0.0          0.0    2.0    1.0               0.0              0.0   
1   0.0     0.0          0.0    0.0    0.0               0.0              0.0   
2   0.0     0.0          0.0    0.0    0.0               0.0              0.0   
3   0.0     0.0          0.0    0.0    1.0               0.0              0.0   
4   0.0     0.0          0.0    0.0    0.0               0.0              0.0   

   vegetables  seasonings  fruits  condiment  liquid  cake_mix  soup  \
0         0.0         0.0     0.0        0.0     1.0       0.0   0.0   
1         1.0         0.0     0.0        1.0     1.0       0.0   1.0   
2         0.0         1.0     0.0        0.0     0.0       0.0   0.0   
3         2.0         0.0     1.0        0.0     0.0       0.0   0.0   
4         0.0         0.0     0.0        0.0     0.0       0.0   0.0   

   oil_vinegar  fish  alcohol  chili  bell_pepper  pie_cookies  chips  \
0          1.0   0.0      0.0    0.0          0.0          0.0    0.0   
1          0.0   0.0      0.0    0.0          0.0          0.0    0.0   
2          0.0   0.0      0.0    0.0          0.0          0.0    0.0   
3          0.0   0.0      0.0    0.0          0.0          0.0    0.0   
4          0.0   0.0      0.0    0.0          0.0          0.0    0.0   

   whipped  cream  rice_noodle  
0      0.0    0.0          0.0  
1      0.0    0.0          0.0  
2      0.0    1.0          0.0  
3      0.0    0.0          0.0  
4      0.0    0.0          0.0

### cereal group

In [172]:
factor2['cereal'] = factor2['cereal']+factor2['cheerios']+factor2['crisp rice cereal']+factor2['granola cereal']+factor2['kellogg']+factor2['kernel corn']+factor2['popcorn']+factor2['rice cereal']+factor2['yellow corn meal']+factor2['yellow cornmeal']

In [173]:
cereal_columns_list = ['cheerios','crisp rice cereal','granola cereal','kellogg','kernel corn','popcorn','rice cereal','yellow corn meal','yellow cornmeal']
len(cereal_columns_list)

9

In [174]:
factor2 = factor2.drop(cereal_columns_list, axis=1)
print(factor2.shape)
factor2.head()

(1000, 44)


item  apples  beans  beef  \
0  [pinto beans, cooking oil, catsup, worcestersh...     0.0    1.0   0.0   
1  [carrots, eggs, grated cheese, cracker crumbs,...     0.0    0.0   0.0   
2  [chicken, cream of chicken, margarine, flour, ...     0.0    0.0   0.0   
3  [pineapple, sugar, lemon flavored gelatin, cre...     1.0    0.0   0.0   
4  [elbow macaroni, grated cheese, eggs, butter, ...     0.0    0.0   0.0   

   bread  butter  cereal  cheese  chicken  chocolate  coconut  corn  crackers  \
0    0.0     0.0     0.0     0.0      0.0        0.0      0.0   0.0       0.0   
1    0.0     0.0     0.0     1.0      0.0        0.0      0.0   0.0       1.0   
2    0.0     2.0     0.0     0.0      1.0        0.0      0.0   0.0       0.0   
3    0.0     0.0     0.0     1.0      0.0        0.0      0.0   0.0       0.0   
4    0.0     1.0     0.0     1.0      0.0        0.0      0.0   0.0       0.0   

   eggs  flour  fruit  lemon  milk  nuts  oranges  pasta  peas  pepper  pork  \
0   0.0    1.0    0.0    0.0   0.0   0.0      0.0    0.0   0.0     0.0   0.0   
1   1.0    0.0    0.0    0.0   0.0   0.0      0.0    0.0   0.0     0.0   0.0   
2   0.0    1.0    0.0    0.0   0.0   0.0      0.0    0.0   0.0     0.0   0.0   
3   0.0    0.0    0.0    1.0   0.0   1.0      0.0    0.0   0.0     0.0   0.0   
4   1.0    0.0    0.0    0.0   1.0   0.0      0.0    1.0   0.0     0.0   0.0   

   potato  sauce  sugar  vegetables  seasonings  fruits  condiment  liquid  \
0     0.0    2.0    1.0         0.0         0.0     0.0        0.0     1.0   
1     0.0    0.0    0.0         1.0         0.0     0.0        1.0     1.0   
2     0.0    0.0    0.0         0.0         1.0     0.0        0.0     0.0   
3     0.0    0.0    1.0         2.0         0.0     1.0        0.0     0.0   
4     0.0    0.0    0.0         0.0         0.0     0.0        0.0     0.0   

   cake_mix  soup  oil_vinegar  fish  alcohol  chili  bell_pepper  \
0       0.0   0.0          1.0   0.0      0.0    0.0          0.0   
1       0.0   1.0          0.0   0.0      0.0    0.0          0.0   
2       0.0   0.0          0.0   0.0      0.0    0.0          0.0   
3       0.0   0.0          0.0   0.0      0.0    0.0          0.0   
4       0.0   0.0          0.0   0.0      0.0    0.0          0.0   

   pie_cookies  chips  whipped  cream  rice_noodle  
0          0.0    0.0      0.0    0.0          0.0  
1          0.0    0.0      0.0    0.0          0.0  
2          0.0    0.0      0.0    1.0          0.0  
3          0.0    0.0      0.0    0.0          0.0  
4          0.0    0.0      0.0    0.0          0.0

In [175]:
factor2.to_csv('data2.csv')